# [0.4] - Build Your Own Backpropagation Framework (exercises)

> **ARENA [Streamlit Page](https://arena-chapter0-fundamentals.streamlit.app/04_[0.4]_Backprop)**
>
> **Colab: [exercises](https://colab.research.google.com/github/callummcdougall/ARENA_3.0/blob/main/chapter0_fundamentals/exercises/part4_backprop/0.4_Backprop_exercises.ipynb?t=20250910) | [solutions](https://colab.research.google.com/github/callummcdougall/ARENA_3.0/blob/main/chapter0_fundamentals/exercises/part4_backprop/0.4_Backprop_solutions.ipynb?t=20250910)**

Please send any problems / bugs on the `#errata` channel in the [Slack group](https://join.slack.com/t/arena-uk/shared_invite/zt-3afdmdhye-Mdb3Sv~ss_V_mEaXEbkABA), and ask any questions on the dedicated channels for this chapter of material.

You can collapse each section so only the headers are visible, by clicking the arrow symbol on the left hand side of the markdown header cells.

Links to all other chapters: [(0) Fundamentals](https://arena-chapter0-fundamentals.streamlit.app/), [(1) Transformer Interpretability](https://arena-chapter1-transformer-interp.streamlit.app/), [(2) RL](https://arena-chapter2-rl.streamlit.app/).

<img src="https://raw.githubusercontent.com/info-arena/ARENA_img/main/misc/headers/header-04.png" width="350">

# Introduction

Today you're going to build your very own system that can run the backpropagation algorithm in essentially the same way as PyTorch does. By the end of the day, you'll be able to train a multi-layer perceptron neural network, using your own backprop system!

The main differences between the full PyTorch and our version are:

* We will focus on CPU only, as all the ideas are the same on GPU.
* We will use NumPy arrays internally instead of ATen, the C++ array type used by PyTorch. Backpropagation works independently of the array type.
* A real `torch.Tensor` has about 700 fields and methods. We will only implement a subset that are particularly instructional and/or necessary to train the MLP.

Note - for today, I'd lean a lot more towards being willing to read the solutions, and even move on from some of them if you don't fully understand them (especially in the first half of section 3). The low-level messy implementation details for today are much less important than the high-level conceptual takeaways.

For a lecture on the material today, which provides some high-level understanding before you dive into the material, watch the video below:

<iframe width="540" height="304" src="https://www.youtube.com/embed/-24lS-kk5I0" frameborder="0" allow="accelerometer; autoplay; encrypted-media; gyroscope; picture-in-picture" allowfullscreen></iframe>

## Content & Learning Objectives

### 1️⃣ Introduction to backprop

This takes you through what a **computational graph** is, and the basics of how gradients can be backpropagated through such a graph. You'll also implement the backwards versions of some basic functions: if we have tensors `output = func(input)`, then the backward function of `func` can calculate the grad of `input` as a function of the grad of `output`.

> ##### Learning Objectives
>
> * Understand what a computational graph is, and how it can be used to calculate gradients.
> * Start to implement backwards versions of some basic functions.

### 2️⃣ Autograd

This section goes into more detail on the backpropagation methodology. In order to find the `grad` of each tensor in a computational graph, we first have to perform a **topological sort** of the tensors in the graph, so that each time we try to calculate `tensor.grad`, we've already computed all the other gradients which are used in this calculation. We end this section by writing a `backprop` function, which works just like the `tensor.backward()` method you're already used to in PyTorch.

> ##### Learning Objectives
>
> * Perform a topological sort of a computational graph (and understand why this is important).
> * Implement a the `backprop` function, to calculate and store gradients for all tensors in a computational graph.

### 3️⃣ Training on MNIST from scratch

In this section, we build your own equivalents of `torch.nn` features like `nn.Parameter`, `nn.Module`, and `nn.Linear`. We can then use these to build our own neural network to classify MINST data.

This completes the chain which starts at basic numpy arrays, and ends with us being able to build essentially any neural network architecture we want!

> ##### Learning Objectives
>
> * Implement more forward and backward functions, including for indexing, summing, and matrix multiplication
> * Learn how to build higher-level abstractions like parameters and modules on top of individual functions and tensors
> * Complete the process of building up a neural network from scratch and training it via gradient descent.

### 4️⃣ Bonus

A few bonus exercises are suggested, for pushing your understanding of backpropagation further.

## Setup code

In [1]:
import os
import sys
from pathlib import Path

IN_COLAB = "google.colab" in sys.modules

chapter = "chapter0_fundamentals"
repo = "ARENA_3.0"
branch = "main"

# Install dependencies
try:
    import jaxtyping
except:
    %pip install einops jaxtyping

# Get root directory, handling 3 different cases: (1) Colab, (2) notebook not in ARENA repo, (3) notebook in ARENA repo
root = (
    "/content"
    if IN_COLAB
    else "/root"
    if repo not in os.getcwd()
    else str(next(p for p in Path.cwd().parents if p.name == repo))
)

if Path(root).exists() and not Path(f"{root}/{chapter}").exists():
    if not IN_COLAB:
        !sudo apt-get install unzip
        %pip install jupyter ipython --upgrade

    if not os.path.exists(f"{root}/{chapter}"):
        !wget -P {root} https://github.com/callummcdougall/ARENA_3.0/archive/refs/heads/{branch}.zip
        !unzip {root}/{branch}.zip '{repo}-{branch}/{chapter}/exercises/*' -d {root}
        !mv {root}/{repo}-{branch}/{chapter} {root}/{chapter}
        !rm {root}/{branch}.zip
        !rmdir {root}/{repo}-{branch}


if f"{root}/{chapter}/exercises" not in sys.path:
    sys.path.append(f"{root}/{chapter}/exercises")

os.chdir(f"{root}/{chapter}/exercises")

In [2]:
import os
import re
import sys
import time
from dataclasses import dataclass
from pathlib import Path
from typing import Any, Callable, Iterable, Iterator

import numpy as np
from torch.utils.data import DataLoader
from tqdm import tqdm

Arr = np.ndarray
grad_tracking_enabled = True

# Make sure exercises are in the path
chapter = "chapter0_fundamentals"
section = "part4_backprop"
root_dir = next(p for p in Path.cwd().parents if (p / chapter).exists())
exercises_dir = root_dir / chapter / "exercises"
section_dir = exercises_dir / section
if str(exercises_dir) not in sys.path:
    sys.path.append(str(exercises_dir))


import part4_backprop.tests as tests
from part4_backprop.utils import get_mnist, visualize
from plotly_utils import line

<details>
<summary>Help - I get a NumPy-related error</summary>

This is an annoying colab-related issue which I haven't been able to find a satisfying fix for. If you restart runtime (but don't delete runtime), and run just the imports cell above again (but not the `%pip install` cell), the problem should go away.
</details>

# 1️⃣ Introduction to backprop

> ##### Learning Objectives
>
> * Understand what a computational graph is, and how it can be used to calculate gradients.
> * Start to implement backwards versions of some basic functions.

## Reading

* [Calculus on Computational Graphs: Backpropagation (Chris Olah)](https://colah.github.io/posts/2015-08-Backprop/)

## Computing Gradients with Backpropagation

This section will briefly review the backpropagation algorithm, but focus mainly on the concrete implementation in software.

To train a neural network, we want to know how the loss would change if we slightly adjust one of the learnable parameters.

One obvious and straightforward way to do this would be just to add a small value  to the parameter, and run the forward pass again. This is called finite differences, and the main issue is we need to run a forward pass for every single parameter that we want to adjust. This method is infeasible for large networks, but it's important to know as a way of sanity checking other methods.

A second obvious way is to write out the function for the entire network, and then symbolically take the gradient to obtain a symbolic expression for the gradient. This also works and is another thing to check against, but the expression gets quite complicated.

Suppose that you have some **computational graph**, and you want to determine the derivative of the some scalar loss L with respect to NumPy arrays a, b, and c:

<img src="https://raw.githubusercontent.com/callummcdougall/Fundamentals/main/images/abc_de_L.png" width="400">

This graph corresponds to the following Python:

```python
d = a * b
e = b + c
L = d + e
```

The goal of our system is that users can write ordinary looking Python code like this and have all the book-keeping needed to perform backpropagation happen behind the scenes. To do this, we're going to wrap each array and each function in special objects from our library that do the usual thing plus build up this graph structure that we need.

### Backward Functions

We've drawn our computation graph from left to right and the arrows pointing to the right, so that in the forward pass, boxes to the right depend on boxes to the left. In the backwards pass, the opposite is true: the gradient of boxes on the left depends on the gradient of boxes on the right.

If we want to compute the derivative of $L$ wrt all other variables (as was described in the reading), we should traverse the graph from right to left. Each time we encounter an instance of function application, we can use the chain rule from calculus to proceed one step further to the left. For example, if we have $d = a \times b$, then:

$$
\frac{dL}{da} = \frac{dL}{dd}\times \frac{dd}{da} = \frac{dL}{dd}\times b
$$

Suppose we are working from right to left, trying to calculate $\frac{dL}{da}$. If we already know the values of the variables $a$, $b$ and $d$, as well as the value of $\frac{dL}{dd}$, then we can use the following function to find $\frac{dL}{da}$:

$$
F\left(a, b, d, \frac{dL}{dd}\right) = \frac{dL}{dd}\times b
$$

and we can do something similar when trying to calculate $\frac{dL}{db}$.

In other words, we can take the **"forward function"** $(a, b) \to a \cdot b$, and for each of its parameters, we can define an associated **"backwards function"** which tells us how to compute the gradient wrt this argument using only known quantities as inputs.

Ignoring issues of unbroadcasting (which we'll cover later), we could write the backward with respect to the first argument as:

```python
def multiply_back(grad_out, out, a, b):
    '''
    Inputs:
        grad_out = dL/d(out)
        out = a * b

    Returns:
        dL/da
    '''
    return grad_out * b
```

where `grad_out` is the gradient of the loss of the function with respect to the output (i.e. $\frac{dL}{dd}$), `out` is the output of the function (i.e. $d$), and `a` and `b` are our inputs.

### Topological Ordering

When we're actually doing backprop, how do we guarantee that we'll always know the value of our backwards functions' inputs? For instance, in the example above we couldn't have computed $\frac{dL}{da}$ without first knowing $\frac{dL}{dd}$.

The answer is that we sort all our nodes using an algorithm called [topological sorting](https://en.wikipedia.org/wiki/Topological_sorting), and then do our computations in this order. After each computation, we store the gradients in our nodes for use in subsequent calculations.

When described in terms of the diagram above, topological sort can be thought of as an ordering of nodes from right to left. Crucially, this sorting has the following property: if there is a directed path in the computational graph going from node `x` to node `y`, then `x` must follow `y` in the sorting.

There are many ways of proving that a cycle-free directed graph contains a topological ordering. You can try and prove this for yourself, or click on the expander below to reveal the outline of a simple proof.

<details>
<summary>Click to reveal proof</summary>

We can prove by induction on the number of nodes $N$.
    
If $N=1$, the problem is trivial.

If $N>1$, then pick any node, and follow the arrows until you reach a node with no directed arrows going out of it. Such a node must exist, or else you would be following the arrows forever, and you'd eventually return to a node you previously visited, but this would be a cycle, which is a contradiction. Once you've found this "root node", you can put it first in your topological ordering, then remove it from the graph and apply the topological sort on the subgraph created by removing this node. By induction, your topological sorting algorithm on this smaller graph should return a valid ordering. If you append the root node to the start of this ordering, you have a topological ordering for the whole graph.
</details>

A quick note on some potentially confusing terminology. We will refer to the "end node" as the **root node**, and the "starting nodes" as **leaf nodes**. For instance, in the diagram at the top of the section, the left nodes `a`, `b` and `c` are the leaf nodes, and `L` is the root node. This might seem odd given it makes the leaf nodes come before the root nodes, but the reason is as follows: *when we're doing the backpropagation algorithm, we start at `L` and work our way back through the graph*. So, by our notation, we start at the root node and work our way out to the leaves.

Another important piece of terminology here is **parent node**. This means the same thing as it does in most other contexts - the parents of node `x` are all the nodes `y` with connections `y -> x` (so in the diagram, `L`'s parents are `d` and `e`).

<details>
<summary>Question - can you think of a reason it might be important for a node to store a list of all of its parent nodes?</summary>

During backprop, we're moving from right to left in the diagram. If a node doesn't store its parent, then there will be no way to get access to that parent node during backprop, so we can't propagate gradients to it.
</details>

The very first node in our topological sort will be $L$, the root node.

### Backpropagation

After all this setup, the backpropagation mechanism becomes pretty straightforward. We sort the nodes topologically, then we iterate over them and call each backward function exactly once in order to accumulate the gradients at each node.

It's important that the grads be accumulated instead of overwritten in a case like value $b$ which has two outgoing edges, since $\frac{dL}{db}$ will then be the sum of two terms. Since addition is commutative it doesn't matter whether we `backward()` the Mul or the Add that depend on $b$ first.

During backpropagation, for each forward function in our computational graph we need to find the partial derivative of the output with respect to each of its inputs. Each partial is then multiplied by the gradient of the loss with respect to the forward functions output (`grad_out`) to find the gradient of the loss with respect to each input. We'll handle these calculations using backward functions.

## Backward function of log

First, we'll write the backward function for `x -> out = log(x)`. This should be a function which, when fed the values `x, out, grad_out = dL/d(out)` returns the value of `dL/dx` just from this particular computational path.

<img src="https://raw.githubusercontent.com/callummcdougall/Fundamentals/main/images/x_log_out.png" width="400">

Note - it might seem strange at first why we need `x` and `out` to be inputs, `out` can be calculated directly from `x`. The answer is that sometimes it is computationally cheaper to express the derivative in terms of `out` than in terms of `x`.

<details>
<summary>Question - can you think of an example function where it would be computationally cheaper to use 'out' than to use 'x'?</summary>

The most obvious answer is the exponential function, `out = e ^ x`. Here, the gradient `d(out)/dx` is equal to `out`. We'll see this when we implement a backward version of `torch.exp` later today.
</details>

### Exercise - implement `log_back`

> ```yaml
> Difficulty: 🔴🔴⚪⚪⚪
> Importance: 🔵🔵🔵⚪⚪
> 
> You should spend up to 5-10 minutes on this exercise.
> ```

You should fill in this function below. Don't worry about division by zero or other edge cases - the goal here is just to see how the pieces of the system fit together.

*This should just be a short, one-line function.*

In [3]:
def log_back(grad_out: Arr, out: Arr, x: Arr) -> Arr:
    """Backwards function for f(x) = log(x)

    grad_out: Gradient of some loss wrt out
    out: the output of np.log(x).
    x: the input of np.log.

    Return: gradient of the given loss wrt x
    """
    # grad_out = dL/d(out)
    # out = np.log(x)
    # dL/dx = dL/d(out) * d(out)/dx = grad_out * 1/x

    return grad_out / x


tests.test_log_back(log_back)

All tests in `test_log_back` passed!


<details>
<summary>Help - I'm not sure what the output of this backward function for log should be.</summary>

By the chain rule, we have:

$$
\frac{dL}{dx} = \frac{dL}{d(\text{out})} \cdot \frac{d(\text{out})}{dx} = \frac{dL}{d(\text{out})} \cdot \frac{d(\log{x})}{dx} = \frac{dL}{d(\text{out})} \cdot \frac{1}{x}
$$

---

(Note - technically, $\frac{d(\text{out})}{dx}$ is a tensor containing the derivatives of each element of $\text{out}$ with respect to each element of $x$, and we should matrix multiply when we use the chain rule. However, since $\text{out} = \log x$ is an elementwise function of $x$, our application of the chain rule here will also be an elementwise multiplication: $\frac{dL}{dx_{ij}} = \frac{dL}{d(\text{out}_{ij})} \cdot \frac{d(\text{out}_{ij})}{dx_{ij}}$. When we get to things like matrix multiplication later, we'll have to be a bit more careful!)
</details>

<details>
<summary>Help - I get <code>ImportError: numpy.core.multiarray failed to import</code></summary>

This is an annoying colab-related error which I haven't been able to find a satisfying fix for. The setup code at the top of this notebook should have installed a version of numpy which works, although you'll have to click "Restart Runtime" (from the Runtime menu) to make this work. Make sure you don't re-run the cell with `pip install`s.

If this still doesn't work, please flag it in the Slack channel errata.
</details>


<details><summary>Solution</summary>

```python
def log_back(grad_out: Arr, out: Arr, x: Arr) -> Arr:
    """Backwards function for f(x) = log(x)

    grad_out: Gradient of some loss wrt out
    out: the output of np.log(x).
    x: the input of np.log.

    Return: gradient of the given loss wrt x
    """
    return grad_out / x
```
</details>

## Backward functions of two tensors

Now we'll implement backward functions for multiple tensors. From this point onwards, we'll be working with vector-valued derivatives, i.e. terms like $\frac{\partial x}{\partial y}$ where $y$ (and possibly $x$) are tensors. To recap what this notation means - these terms are tensors where each value is the scalar derivative of one of the elements of $x$ wrt one of the elements of $y$. For example:

- If $x$ is a scalar and $y$ is a tensor with shape `(3, 4)`, then $\frac{\partial x}{\partial y}$ is a tensor with shape `(3, 4)` where the `[i, j]`-th element is $\frac{\partial x}{\partial y[i, j]}$, i.e. the derivative of $x$ wrt a particular element of $y$.
- If $x$ is a length-5 vector and $y$ is a tensor with shape `(3, 4)` then $\frac{\partial x}{\partial y}$ is a tensor with shape `(5, 3, 4)` where the `[i, j, k]`-th element is $\frac{\partial x[i]}{\partial y[j, k]}$.

### Broadcasting

Before we go through the next exercises, we'll need to address one important topic in tensor operations - **broadcasting**. We've discussed it in earlier exercises, but we're reviewing it here because it's very important for backprop. If you're comfortable with the topic, feel free to jump forwards to the section "Why do we need broadcasting for backprop?".

Both NumPy and PyTorch have the same rules for broadcasting. When two tensors are involved in an elementwise operation, NumPy/PyTorch tries to broadcast them (i.e. copying them along dimensions) so that they both have the same shape. The rules of broadcasting are as follows:

1. You can prepend dummy dimensions (of size 1) to the start of a tensor until both have the same number of dimensions
2. After this point, if some dimension has size 1 in one of the tensors, it can be repeated until it matches the size of the corresponding dimension in the other tensor

To give a simple example - suppose we have a 2D batch of data, of shape `data.shape = (N, k)` (i.e. we have `N` separate datapoints, each being a vector of length `k`). Suppose we want to add a vector `vec` of length `k` to each datapoint. This is a valid operation, because when we try and add these two objects together:

1. `vec` gets prepended with a dummy dimension so it has shape `(1, k)` and both are 2D
2. `vec` gets repeated along the first dimension so it has shape `(N, k)`, matching the shape of `data`

Then, our output has shape `(N, k)`, and elements `output[i, j] = data[i, j] + vec[j]`.

Broadcasting can be a very easy place to make mistakes, because it's easy to lose track of the exact shape of your tensors involved. As a warm-up exercise, below are some examples of broadcasting. Can you figure out which are valid, and which will raise errors?


```python
x = np.ones((3, 1, 5))
y = np.ones((1, 4, 5))

z = x + y
```

<details>
<summary>Answer</summary>

This is valid, because the 0th dimension of `y` and the 1st dimension of `x` can both be copied so that `x` and `y` have the same shape: `(3, 4, 5)`. The resulting array `z` will also have shape `(3, 4, 5)`.

This example illustrates an important point - it's not always the case that one of the tensors is strictly smaller and the other is strictly bigger. Sometimes, both tensors will get expanded. 

</details>

```python
x = np.ones((8, 2, 6))
y = np.ones((8, 2))

z = x + y
```

<details>
<summary>Answer</summary>

This is not valid. We first need to expand `y` by appending a dimension to the front, and the last two dimensions of `x` are `(2, 6)`, which won't broadcast with `y`'s `(8, 2)`.
</details>

```python
x = np.ones((8, 2, 6))
y = np.ones((2, 6))

z = x + y
```

<details>
<summary>Answer</summary>

This is valid. Once NumPy expands `y` by appending a single dimension to the front, it can then be broadcast with `x`.
</details>

```python
x = np.ones((10, 20, 30))
y = np.ones((20, 1))

z = x + y
```

<details>
<summary>Answer</summary>

This is valid. Once NumPy expands `y` by appending a single dimension to the front, it can then be broadcast with `x` (this will involve copying along the first and last dimensions).
</details>

```python
x = np.ones((4, 1))
y = np.ones((4,))

z = x + y
```

<details>
<summary>Answer</summary>

This is valid. Numpy will expand the second one to `(1, 4)` then broadcast them both to `(4, 4)`.

Although this won't raise an error, it's very possible that this isn't what the person adding these two arrays intended. A common source of mistakes is when you add 2 tensors thinking they're the same shape, but one actually has a dummy dimension you forgot about. Sadly this is something you'll just have to be vigilant for (e.g. adding assert statements where necessary, or making sure you aren't combining too many different tensor operations in a single line), because PyTorch doesn't have built-in ways of statically checking your tensor shapes.

</details>

### Why do we need broadcasting for backprop?

Often, operations like `out = f(x, y)` involve an implicit broadcasting step. For example, if `out = x + y` with `x.shape = (4,)` and `y.shape = (3, 4)`, then really our operation has 2 steps:

1. Broadcast `x` to a broadcasted version `x_b` which has the shape of `y`, i.e. copy it along the zeroth dimension to have shape `(3, 4)`,
2. Define `out = x_b + y`, which is an operation that doesn't involve broadcasting.

<img src="https://raw.githubusercontent.com/info-arena/ARENA_img/main/misc/broadcast-last-1.png" width="600">

How can we go from the gradient `dL/d(x_b)` (which might be easy to compute given it involves no broadcasting) to the gradient of `dL/dx`? The answer is that **we take `dL/d(x_b)` and sum it over the dimensions along which `x` was broadcasted to get `dL/dx`.**

For the mathematically inclined this can be proved fairly easily (we provide a sketch of the proof below). But let's focus on the intuition here. When we copy `x` along axes to create `x_b`, we're essentially creating multiple pathways for each element of `x` to affect the final loss: one path for each time the element of `x` was copied. So when we change some element of `x`, this causes a first-order change in the loss from all of these different pathways, and we have to sum these changes to get the total first-order change (i.e. the derivative). For example:

<img src="https://raw.githubusercontent.com/info-arena/ARENA_img/main/misc/broadcast-last-2.png" width="540">

> ##### Summary
>
> If we know $\frac{\partial L}{\partial (\mathbf{out})}$, and want to know $\frac{\partial L}{\partial \mathbf{x}}$ (where $x$ was broadcasted to produce $\text{out}$) then there are two steps:
>
> 1. Compute $\frac{\partial L}{\partial \mathbf{x_b}}$ in the standard way, i.e. using one of your backward functions (assuming no broadcasting happened).
> 2. ***Unbroadcast*** $\frac{\partial L}{\partial \mathbf{x_b}}$, by summing it over the dimensions along which $\mathbf{x}$ was broadcasted.


<details>
<summary>Mathematical derivation (sketch)</summary>

We start with:

$$
\frac{\partial L}{\partial \mathbf{x}} = \sum_{i_1, i_2, ...} \frac{\partial L}{\partial x_b[i_1, i_2, ...]} \cdot \frac{\partial x_b[i_1, i_2, ...]}{\partial \mathbf{x}}
$$

using the chain rule. Next, we can use the fact that $\frac{\partial x_b[i_1, i_2, ...]}{\partial x[j_1, j_2, ...]}$ equals 0 everywhere except the indices where $x$ was broadcasted to produce $x_b$, where it equals 1. Therefore, this sum over indices $i_1, i_2, ...$ is equivalent to just summing $\frac{\partial L}{\partial x_b[i_1, i_2, ...]}$ over the repeated elements of $x$.

</details>

We used the term "unbroadcast" because the way that our tensor's shape changes will be the reverse of how it changed during broadcasting. If `x` was broadcasted from `(4,) -> (3, 4)`, then unbroadcasting will have to take a tensor of shape `(3, 4)` and sum over it to return a tensor of shape `(4,)`. Similarly, if `x` was broadcasted from `(1, 4) -> (3, 4)`, then we need to sum over the zeroth dimension, but leave it as a 2D tensor with a leading dummy dimension of size 1.

### Exercise - implement `unbroadcast`

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵🔵⚪⚪
> 
> You should spend up to 10-25 minutes on this exercise.
> This function can be quite fiddly - if you're stuck, read and understand the solution code instead.
> ```

The `unbroadcast` function below should take any value like $\frac{\partial L}{\partial x_b}$ and return $\frac{\partial L}{\partial x}$ (where the arguments `original` and `broadcasted` represent $x$ and $x_b$ respectively). In the same way that broadcasting `original` to the shape of `broadcasted` can be described as a 2-step process:

1. Extend dummy dimensions (size 1) of `original` to match the last dimensions of `broadcasted`,
2. Prepend dimensions to `original` until it has the same ndims as `broadcasted`,

the unbroadcasting process is the same process in reverse:

1. Sum over prepended dimensions of `broadcasted` until it has the same ndims as `original`,
2. Now they have the same ndims, sum over dimensions of `broadcasted` where `original` had size 1.

For example, if `original.shape = (3, 1)` and `broadcasted.shape = (1, 2, 3, 4)` then the broadcasting steps look like `(3, 1) -> (3, 4) -> (1, 2, 3, 4)` (copying along those dimensions at each step) and the unbroadcasting steps look like `(1, 2, 3, 4) -> (3, 4) -> (3, 1)` (summing over those dimensions at each step).

In [4]:
def unbroadcast(broadcasted: Arr, original: Arr) -> Arr:
    """
    Sum 'broadcasted' until it has the shape of 'original'.

    broadcasted: An array that was formerly of the same shape of 'original' and was expanded by
        broadcasting rules.
    """
    # YOUR CODE HERE: sum over `broadcasted` until it has the shape of `original`
    added_dims = len(broadcasted.shape) - len(original.shape)
    added_dims = tuple(range(added_dims))
    broadcasted = broadcasted.sum(axis=added_dims)

    for i in range(len(broadcasted.shape)):
        if broadcasted.shape[i] > 1 and original.shape[i] == 1:
            broadcasted = broadcasted.sum(axis=i, keepdims=True)

    assert broadcasted.shape == original.shape
    return broadcasted


tests.test_unbroadcast(unbroadcast)

All tests in `test_unbroadcast` passed!


<details><summary>Solution</summary>

```python
def unbroadcast(broadcasted: Arr, original: Arr) -> Arr:
    """
    Sum 'broadcasted' until it has the shape of 'original'.

    broadcasted: An array that was formerly of the same shape of 'original' and was expanded by
        broadcasting rules.
    """
    # Step 1: sum and remove prepended dims, so both arrays have same number of dims
    n_dims_to_sum = len(broadcasted.shape) - len(original.shape)
    broadcasted = broadcasted.sum(axis=tuple(range(n_dims_to_sum)))

    # Step 2: sum over dims which were originally 1 (but don't remove them)
    dims_to_sum = tuple(
        [i for i, (o, b) in enumerate(zip(original.shape, broadcasted.shape)) if o == 1 and b > 1]
    )
    broadcasted = broadcasted.sum(axis=dims_to_sum, keepdims=True)

    assert broadcasted.shape == original.shape
    return broadcasted
```
</details>

### Backward Function for Elementwise Multiply

Functions that are differentiable with respect to more than one input tensor are straightforward given that we already know how to handle broadcasting.

- We're going to have two backwards functions, one for each input argument.
- If the input arguments were broadcasted together to create a larger output, the incoming `grad_out` will be of the larger common broadcasted shape and we need to make use of `unbroadcast` from earlier to match the shape to the appropriate input argument.
- We'll want our backward function to work when one of the inputs is a float (as opposed to a tensor). We won't need to calculate the grad_in with respect to floats, so we only need to consider when y is a float for `multiply_back0` and when x is a float for `multiply_back1`.

### Exercise - implement both `multiply_back` functions

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵⚪⚪⚪
> 
> You should spend up to 10-15 minutes on these exercises.
> ```

Below, you should implement both `multiply_back0` and `multiply_back1`.

You might be wondering why we need two different functions, rather than just having a single function to serve both purposes. This will become more important later on, once we deal with functions with more than one argument, which is not symmetric in its arguments. For instance, the derivative of $x / y$ wrt $x$ is not the same as the expression you get after differentiating this wrt $y$ then swapping the labels around.

The first part of each function has been provided for you (this makes sure that both inputs are arrays, since we want to support multiplication by floats or scalars).

In [5]:
def multiply_back0(grad_out: Arr, out: Arr, x: Arr, y: Arr | float) -> Arr:
    """Backwards function for x * y wrt argument 0 aka x."""
    if not isinstance(y, Arr):
        y = np.array(y)

    return unbroadcast(grad_out * y, x) 

def multiply_back1(grad_out: Arr, out: Arr, x: Arr | float, y: Arr) -> Arr:
    """Backwards function for x * y wrt argument 1 aka y."""
    if not isinstance(x, Arr):
        x = np.array(x)

    return unbroadcast(grad_out * x, y)


tests.test_multiply_back(multiply_back0, multiply_back1)
tests.test_multiply_back_float(multiply_back0, multiply_back1)

All tests in `test_multiply_back` passed!
All tests in `test_multiply_back_float` passed!


<details>
<summary>Hint</summary>

Using the chain rule for scalar functions, we can find that:

$$
\frac{\partial L}{\partial x} = \frac{\partial L}{\partial (xy)} \cdot \frac{\partial (xy)}{\partial x} = \frac{\partial L}{\partial (xy)} \cdot y
$$

An equivalent result\* holds for vector-valued inputs:

$$
\frac{\partial L}{\partial \mathbf{x}_b} = \frac{\partial L}{\partial (\mathbf{x}_b \cdot \mathbf{y}_b)} \cdot \mathbf{y}_b
$$

where $\cdot$ is the elementwise multiplication operator, and $\mathbf{x}_b, \mathbf{y}_b$ are the broadcasted versions of the input tensors. This allows us to compute $\frac{\partial L}{\partial \mathbf{x}_b}$ based on the inputs to our `multiply_back0` function. Can you use `unbroadcast` to finish the calculation?

\*You can derive this result for yourself using the chain rule. Note that application of the chain rule here would require you to sum over the elements of the intermediate tensor $\mathbf{x}_b \cdot \mathbf{y}_b$, but we're working with elementwise operations so $\partial (\mathbf{x}_b \cdot \mathbf{y}_b)[i_1, i_2, ...] / \partial \mathbf{x}_b$ will have all elements zero except for one and the sum falls out, leaving us with the result above.

</details>

<details>
<summary>Solution (and explanation)</summary>

Based on the discussion in hint 1, we can conclude that the value $\partial L / \partial \mathbf{x}_b$ is equal to `y_b * grad_out`. Note that this is just equivalent to `y * grad_out` because `y` will be broadcasted to the shape of `y_b` when we multiply it with `grad_out` (since we know `grad_out` has the same shape as the broadcasted `x * y` tensor).

Now, we need to go from this broadcasted derivative to the shape of `x`, and we do this by applying `unbroadcast`, summing `y * grad_out` over dimensions so that it's the same shape as `x` - in other words, we return `unbroadcast(y * grad_out, x)`.

The output of `multiply_back1` is the same as `multiply_back0`, except the roles of `x` and `y` are reversed.

```python
def multiply_back0(grad_out: Arr, out: Arr, x: Arr, y: Arr | float) -> Arr:
    """Backwards function for x * y wrt argument 0 aka x."""
    if not isinstance(y, Arr):
        y = np.array(y)

    return unbroadcast(y * grad_out, x)


def multiply_back1(grad_out: Arr, out: Arr, x: Arr | float, y: Arr) -> Arr:
    """Backwards function for x * y wrt argument 1 aka y."""
    if not isinstance(x, Arr):
        x = np.array(x)

    return unbroadcast(x * grad_out, y)
```

<!-- Derivation: first we compute the gradient of the broadcasted tensor, using the chain rule:

$$
\frac{\partial L}{\partial x_b[i_1, i_2, ...]} = \frac{\partial L}{\partial (x_b \cdot y_b)[i_1, i_2, ...]} \cdot \frac{\partial (x_b \cdot y_b)[i_1, i_2, ...]}{\partial x_b[i_1, i_2, ...]}
$$

where we've avoided the sum over indices of $x_b \cdot y_b$ because this is an elementwise operation, and so those gradients must be zero everywhere except where all $i_k = j_k$. We can further write this as:

$$
\frac{\partial L}{\partial x_b[i_1, i_2, ...]} = \text{grad\_out}[i_1, i_2, ...] \cdot y[i_1, i_2, ...]
$$

which gives us the result for broadcasted tensors! Note that although this tensor is `grad_out * y_b`, we can compute it as `grad_out * y` because we know that `y` is broadcastable to the shape of `grad_out` (since this is also the same as the shape of `out`).

Once we have this result `grad_out * y`, we just use `unbroadcast` to sum over the dimensions `x` was broadcasted along.  -->

</details>

Now we'll use our backward functions to do backpropagation manually, for the following computational graph:

<img src="https://raw.githubusercontent.com/callummcdougall/Fundamentals/main/images/abcdefg.png" width=550>

### Exercise - implement `forward_and_back`

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵🔵🔵⚪
> 
> You should spend up to 15-20 minutes on these exercises.
> This function is very useful for getting a sense for what backprop looks like in practice.
> ```

Below, you should implement the `forward_and_back` function. This is an opportunity for you to practice using the backward functions you've written so far, and should hopefully give you a better sense of how the full backprop function will eventually work.

Note - you might be wondering what `grad_out` should be the first time you call a backward function. We've so far assumed that the final node `L` in the computational graph is a scalar, and all gradients (i.e. the `grad_out` input to our backward functions and the output of our backward functions) are gradients of `L`. In this case, it would make sense to set `grad_out = [1]` for the first backward function call, since we're computing $\frac{\partial L}{\partial L} = 1$. But what about cases like the one above, when our final node `g` might not be a scalar?

The answer is that we effectively add a final scalar node into our graph, defined as `L = (g * v).sum()` for some tensor `v` of the same shape as `g`. This is called the **directional derivative**. We then compute all tensor gradients using `L` as our final node. For example, this means that in our first gradient calculation (where `g` is the output and `f` is the input) we'll use `grad_out = dL/dg = v`. You don't really need to worry about this, because most of the time (including in the exercise below) we'll just be using the default behaviour where `v` is a tensor of 1s - this is equivalent to `L = g.sum()`.

In [6]:
def forward_and_back(a: Arr, b: Arr, c: Arr) -> tuple[Arr, Arr, Arr]:
    """
    Calculates the output of the computational graph above (g), then backpropogates the gradients
    and returns dg/da, dg/db, and dg/dc.
    """
    d = a * b
    e = np.log(c)
    f = d * e
    g = np.log(f)
    final_grad_out = np.ones_like(g)

    # YOUR CODE HERE - use your backward functions to compute the gradients of g wrt a, b, and c

    """
    g = log(f)
    dg/df = 1/f
    
    f = d * e
    dg_dd = dg_df * df_dd
    """
    dg_df = log_back(final_grad_out, g, f)

    dg_dd = multiply_back0(dg_df, f, d, e)
    dg_de = multiply_back1(dg_df, f, d, e)
    
    dg_da = multiply_back0(dg_dd, d, a, b)
    dg_db = multiply_back1(dg_dd, d, a, b)

    dg_dc = log_back(dg_de, e, c)

    return (dg_da, dg_db, dg_dc)


tests.test_forward_and_back(forward_and_back)

All tests in `test_forward_and_back` passed!


<details><summary>Solution</summary>

```python
def forward_and_back(a: Arr, b: Arr, c: Arr) -> tuple[Arr, Arr, Arr]:
    """
    Calculates the output of the computational graph above (g), then backpropogates the gradients
    and returns dg/da, dg/db, and dg/dc.
    """
    d = a * b
    e = np.log(c)
    f = d * e
    g = np.log(f)
    final_grad_out = np.ones_like(g)

    dg_df = log_back(grad_out=final_grad_out, out=g, x=f)
    dg_dd = multiply_back0(dg_df, f, d, e)
    dg_de = multiply_back1(dg_df, f, d, e)
    dg_da = multiply_back0(dg_dd, d, a, b)
    dg_db = multiply_back1(dg_dd, d, a, b)
    dg_dc = log_back(dg_de, e, c)

    return (dg_da, dg_db, dg_dc)
```
</details>

In the next section, you'll build up to full automation of this backpropagation process, in a way that's similar to PyTorch's `autograd`.

# 2️⃣ Autograd

> ##### Learning Objectives
>
> * Perform a topological sort of a computational graph (and understand why this is important).
> * Implement a the `backprop` function, to calculate and store gradients for all tensors in a computational graph.

Now, rather than figuring out which backward functions to call, in what order, and what their inputs should be, we'll write code that takes care of that for us. We'll implement this with a few major components:

- `Tensor`, which is a wrapper around numpy arrays which is equivalent to PyTorch's `Tensor` class
- `Recipe`, which tracks the extra information needed to run backpropagation (mainly how this tensor was created from other tensors)
- `wrap_forward_fn`, which takes a numpy function mapping arrays to arrays (e.g. `np.log`) and returns a new function that maps tensors to tensors (while also creating the recipe for the new tensor)

## Wrapping Arrays (Tensor)

We're going to wrap each array with a wrapper object from our library which we'll call `Tensor` because it's going to behave similarly to a `torch.Tensor`.

Each Tensor that is created by one of our forward functions will have a `Recipe`, which tracks the extra information need to run backpropagation.

`wrap_forward_fn` will take a forward function and return a new forward function that does the same thing while recording the info we need to do backprop in the `Recipe`.

## Recipe

Let's start by taking a look at `Recipe`.

`@dataclass` is a handy class decorator that sets up an `__init__` function for the class that takes the provided attributes as arguments and sets them as you'd expect.

The class `Recipe` is designed to track the forward functions in our computational graph, so that gradients can be calculated during backprop. Each tensor created by a forward function has its own `Recipe`. We're naming it this because it is a set of instructions that tell us which ingredients went into making our tensor: what the function was, and what tensors were used as input to the function to produce this one as output.

In [7]:
@dataclass(frozen=True)
class Recipe:
    """Extra information necessary to run backpropagation. You don't need to modify this."""

    func: Callable
    "The 'inner' NumPy function that does the actual forward computation."
    "Note, we call it 'inner' to distinguish it from the wrapper we'll create for it later on."

    args: tuple
    "The input arguments passed to func."
    "For instance, if func=np.sum then args would be a length-1 tuple with the tensor to be summed."

    kwargs: dict[str, Any]
    "Keyword arguments passed to func."
    "For instance, if func was np.sum then kwargs might contain 'dim' and 'keepdims'."

    parents: dict[int, "Tensor"]
    "Map from positional argument index to the Tensor at that position."
    "For passing gradients back along the computational graph."

Note that `args` just stores the values of the underlying arrays, but `parents` stores the actual tensors. This is because they serve two different purposes: `args` is required for computing the value of gradients during backpropagation, and `parents` is required to infer the structure of the computational graph (i.e. which tensors were used to produce which other tensors).

Here are some examples, to build intuition for what the four fields of `Recipe` are, and why we need all four of them to fully describe a tensor in our graph and how it was created. Make sure you understand each of these examples before moving on, because it'll really help you progress quickly through the following exercises.

<img src="https://raw.githubusercontent.com/info-arena/ARENA_img/main/misc/recipe-v2.png" width="800">

## Registering backwards functions

The `Recipe` takes care of tracking the forward functions in our computational graph, but we still need a way to find the backward function corresponding to a given forward function when we do backprop (or possibly the set of backward functions, if the forward function takes more than one argument).

### Exercise - implement `BackwardFuncLookup`

> ```yaml
> Difficulty: 🔴🔴⚪⚪⚪
> Importance: 🔵🔵🔵⚪⚪
> 
> You should spend up to 10-15 minutes on these exercises.
> These exercises should be very short, once you understand what is being asked.
> ```

We will define a class `BackwardFuncLookup` in order to find the backward function for a given forward function. The implementation details are left up to you - all that matters is that you pass the test code in the cell below. Reading this test code should explain how the `BackwardFuncLookup` class needs to be used - for any given forward function e.g. `np.log`, we need to be able to add a set of backward functions for each of its positional arguments.

In [8]:
class BackwardFuncLookup:
    def __init__(self) -> None:
        self.data = {}

    def add_back_func(self, forward_fn: Callable, arg_position: int, back_fn: Callable) -> None:
        self.data[(forward_fn, arg_position)] = back_fn

    def get_back_func(self, forward_fn: Callable, arg_position: int) -> Callable:
        return self.data[(forward_fn, arg_position)]


BACK_FUNCS = BackwardFuncLookup()

BACK_FUNCS.add_back_func(np.log, 0, log_back)
BACK_FUNCS.add_back_func(np.multiply, 0, multiply_back0)
BACK_FUNCS.add_back_func(np.multiply, 1, multiply_back1)

assert BACK_FUNCS.get_back_func(np.log, 0) == log_back
assert BACK_FUNCS.get_back_func(np.multiply, 0) == multiply_back0
assert BACK_FUNCS.get_back_func(np.multiply, 1) == multiply_back1

print("Tests passed - BackwardFuncLookup class is working as expected!")

Tests passed - BackwardFuncLookup class is working as expected!


<details>
<summary>Help - I'm stuck on this implementation</summary>

You can define a dict like `self.back_funcs` in the `__init__` method. When you add / retrieve a function, you can use the tuple `(forward_fn, arg_position)` as a key, and the backward function as the value.

</details>


<details><summary>Solution</summary>

```python
class BackwardFuncLookup:
    def __init__(self) -> None:
        self.back_funcs = {}  # each entry is a tuple of (forward_fn, arg_position) -> back_fn

    def add_back_func(self, forward_fn: Callable, arg_position: int, back_fn: Callable) -> None:
        self.back_funcs[(forward_fn, arg_position)] = back_fn

    def get_back_func(self, forward_fn: Callable, arg_position: int) -> Callable:
        return self.back_funcs[(forward_fn, arg_position)]
```

</details>

## Tensors

Our Tensor object has these fields:

- An `array` field of type `np.ndarray`. These are the actual tensor values.
- A `requires_grad` field of type `bool`. This determines whether we need to compute gradients for this tensor (note this doesn't necessarily mean we need to store them, see below).
- A `grad` field of the same size and type as the value. This is where gradients are stored.
- A `recipe` field, as we've already seen. A tensor has a recipe if and only if it was created by some operation on other tensors.

### `requires_grad` and `is_leaf`

The meaning of `requires_grad` is that when doing operations using this tensor, the recipe will be stored and it and any descendents will be included in the computational graph. Note that `requires_grad` does not necessarily mean that we will save the accumulated gradients to this tensor's `.grad` parameter when doing backprop - for example we require gradients to propagate through the hidden activations of a neural network to get back to grads for our model weights, but we don't need to actually store the gradients of the hidden activations.

We use `is_leaf` to differentiate between these cases (see the method `Tensor.is_leaf` defined below) - a leaf tensor is one that represents the end of a backprop path, either because it doesn't require gradients or it has no nodes further back in the computational graph which require gradients. So our backprop algorithm will always terminate at a leaf node, then store that leaf node's gradient as `.grad` only if `requires_grad` is true.

<img src="https://raw.githubusercontent.com/info-arena/ARENA_img/main/misc/is_leaf.png" width="900">

You can investigate this by running the following code:

```python
layer = torch.nn.Linear(3, 4)
input = torch.ones(3)
output = layer(input)

print(layer.weight.is_leaf)       # -> True
print(layer.weight.requires_grad) # -> True

print(output.is_leaf)             # -> False
print(output.requires_grad)       # -> True

print(input.is_leaf)              # -> True
print(input.requires_grad)        # -> False
```

When creating tensors, we can set `requires_grad` explicitly (e.g. it's false by default for most tensors, but is true by default if that tensor is wrapped in `torch.nn.Parameter` - we'll create our own version of this later). When creating a tensor from another tensor or tensors, `requires_grad` is true if and only if all of the following 3 conditions hold:

1. Global grad tracking is enabled. In this notebook we've represented this with the global variable `grad_tracking_enabled`, but in PyTorch this is done with `torch.set_grad_enabled(False)`. This is useful because when you're looking at a model in inference mode, gradient tracking can waste memory and it's useful to disable it (we'll do this a lot next week, when we study transformer interpretability).
2. At least one of the input tensors requires grad (since this is equivalent to "there are other tensors further upstream which we need to get gradients for").
3. The function is differentiable (if not, obviously we can't compute gradients).

Now, we're giving you the full `Tensor` class. Most of these methods are currently undefined, and you'll go on to define them in later exercises (so you won't need to write any code this class). For now, just pay attention to the docstring & `__init__` methods.

In [9]:
Arr = np.ndarray


class Tensor:
    """
    A drop-in replacement for torch.Tensor supporting a subset of features.
    """

    array: Arr
    "The underlying array. Can be shared between multiple Tensors."
    requires_grad: bool
    "If True, calling functions or methods on this tensor will track relevant data for backprop."
    grad: "Tensor | None"
    "Backpropagation will accumulate gradients into this field."
    recipe: "Recipe | None"
    "Extra information necessary to run backpropagation."

    def __init__(self, array: Arr | list, requires_grad=False):
        self.array = array if isinstance(array, Arr) else np.array(array)
        if self.array.dtype == np.float64:
            self.array = self.array.astype(np.float32)
        self.requires_grad = requires_grad
        self.grad = None
        self.recipe = None
        "If not None, this tensor's array was created as recipe.func(*recipe.args, **recipe.kwargs)."

    def __neg__(self) -> "Tensor":
        return negative(self)

    def __add__(self, other) -> "Tensor":
        return add(self, other)

    def __radd__(self, other) -> "Tensor":
        return add(other, self)

    def __sub__(self, other) -> "Tensor":
        return subtract(self, other)

    def __rsub__(self, other) -> "Tensor":
        return subtract(other, self)

    def __mul__(self, other) -> "Tensor":
        return multiply(self, other)

    def __rmul__(self, other):
        return multiply(other, self)

    def __truediv__(self, other):
        return true_divide(self, other)

    def __rtruediv__(self, other):
        return true_divide(other, self)

    def __matmul__(self, other):
        return matmul(self, other)

    def __rmatmul__(self, other):
        return matmul(other, self)

    def __eq__(self, other):
        return eq(self, other)

    def __repr__(self) -> str:
        return f"Tensor({repr(self.array)}, requires_grad={self.requires_grad})"

    def __len__(self) -> int:
        if self.array.ndim == 0:
            raise TypeError
        return self.array.shape[0]

    def __hash__(self) -> int:
        return id(self)

    def __getitem__(self, index) -> "Tensor":
        print(self, index)
        return getitem(self, index)

    def add_(self, other: "Tensor", alpha: float = 1.0) -> "Tensor":
        add_(self, other, alpha=alpha)
        return self

    def sub_(self, other: "Tensor", alpha: float = 1.0) -> "Tensor":
        sub_(self, other, alpha=alpha)
        return self

    def __iadd__(self, other: "Tensor") -> "Tensor":
        self.add_(other)
        return self

    def __isub__(self, other: "Tensor") -> "Tensor":
        self.sub_(other)
        return self

    @property
    def T(self) -> "Tensor":
        return permute(self, axes=(-1, -2))

    def item(self):
        return self.array.item()

    def sum(self, dim=None, keepdim=False) -> "Tensor":
        return sum(self, dim=dim, keepdim=keepdim)

    def log(self) -> "Tensor":
        return log(self)

    def exp(self) -> "Tensor":
        return exp(self)

    def reshape(self, new_shape) -> "Tensor":
        return reshape(self, new_shape)

    def permute(self, dims) -> "Tensor":
        return permute(self, dims)

    def maximum(self, other) -> "Tensor":
        return maximum(self, other)

    def relu(self) -> "Tensor":
        return relu(self)

    def argmax(self, dim=None, keepdim=False) -> "Tensor":
        return argmax(self, dim=dim, keepdim=keepdim)

    def uniform_(self, low: float, high: float) -> "Tensor":
        self.array[:] = np.random.uniform(low, high, self.array.shape)
        return self

    def backward(self, end_grad: "Arr | Tensor | None" = None) -> None:
        if isinstance(end_grad, Arr):
            end_grad = Tensor(end_grad)
        return backprop(self, end_grad)

    def size(self, dim: int | None = None):
        if dim is None:
            return self.shape
        return self.shape[dim]

    @property
    def shape(self):
        return self.array.shape

    @property
    def ndim(self):
        return self.array.ndim

    @property
    def is_leaf(self):
        """Same as https://pytorch.org/docs/stable/generated/torch.Tensor.is_leaf.html"""
        if self.requires_grad and self.recipe and self.recipe.parents:
            return False
        return True

    def __bool__(self):
        if np.array(self.shape).prod() != 1:
            raise RuntimeError("bool value of Tensor with more than one value is ambiguous")
        return bool(self.item())


def empty(*shape: int) -> Tensor:
    """Like torch.empty."""
    return Tensor(np.empty(shape))


def zeros(*shape: int) -> Tensor:
    """Like torch.zeros."""
    return Tensor(np.zeros(shape))


def arange(start: int, end: int, step=1) -> Tensor:
    """Like torch.arange(start, end)."""
    return Tensor(np.arange(start, end, step=step))


def tensor(array: Arr, requires_grad=False) -> Tensor:
    """Like torch.tensor."""
    return Tensor(array, requires_grad=requires_grad)

## Forward Pass: Building the Computational Graph

Let's start with a simple case: our `log` function. `log_forward` is a wrapper, which should implement the functionality of `np.log` but work with tensors rather than arrays.

### Exercise - implement `log_forward`

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵🔵⚪⚪
> 
> You should spend up to 15-20 minutes on this exercise.
> ```

Your `log` function should be a wrapper around `np.log`, which takes and returns a `Tensor` object rather than numpy arrays. You can refer to the first of the five diagrams at the start of the "Recipe" section if you're stuck.

Some more hints / tips:

- As a reminder, `requires_grad` is true if both global gradient tracking is enabled (i.e. `grad_tracking_enabled` is true) and at least one of the inputs has `requires_grad` true.
- You should also set the recipe for the new tensor, if `requires_grad` is true (if not then you can just set the recipe to None).

Later we'll write code to wrap numpy functions in a generic and reusable way, but for now we just want to get this working for `np.log`.

In [10]:
def log_forward(x: Tensor) -> Tensor:
    """Performs np.log on a Tensor object."""
    arr = np.log(x.array)
    req_grad = (grad_tracking_enabled and x.requires_grad)
    ret = Tensor(arr, req_grad)

    if req_grad:
        ret.recipe = Recipe(np.log, (x.array,), {}, {0: x})
    return ret


log = log_forward
tests.test_log(Tensor, log_forward)
tests.test_log_no_grad(Tensor, log_forward)
a = Tensor([1], requires_grad=True)
grad_tracking_enabled = False
b = log_forward(a)
grad_tracking_enabled = True
assert not b.requires_grad, "should not require grad if grad tracking globally disabled"
assert b.recipe is None, "should not create recipe if grad tracking globally disabled"

All tests in `test_log` passed!
All tests in `test_log_no_grad` passed!


<details><summary>Solution</summary>

```python
def log_forward(x: Tensor) -> Tensor:
    """Performs np.log on a Tensor object."""
    # Get the function output (as a numpy array)
    array = np.log(x.array)

    # Find whether the tensor requires grad
    requires_grad = grad_tracking_enabled and x.requires_grad

    # Create the tensor
    out = Tensor(array, requires_grad)

    # Set the recipe (if we need it)
    if requires_grad:
        out.recipe = Recipe(func=np.log, args=(x.array,), kwargs={}, parents={0: x})

    return out
```
</details>

Now let's do the same for multiply, to see how to handle functions with multiple arguments.

### Exercise - implement `multiply_forward`

> ```yaml
> Difficulty: 🔴🔴🔴🔴⚪
> Importance: 🔵🔵🔵⚪⚪
> 
> You should spend up to 15-20 minutes on this exercise.
> ```

There are a few differences between this and log:

- The actual function to be called is different
- We need more than one argument in `args` and `parents`, when defining `Recipe`
- `requires_grad` should be true if `grad_tracking_enabled=True`, and ANY of the input tensors require grad
- One of the inputs may be an int, so you'll need to deal with this case before calculating `out`

If you're confused, you can scroll up to the diagram at the top of the page (which tells you how to construct the recipe for functions like multiply or add when they are both arrays, or when one is an array and the other is a scalar).

In [11]:
def multiply_forward(a: Tensor | int, b: Tensor | int) -> Tensor:
    """Performs np.multiply on a Tensor object."""
    assert isinstance(a, Tensor) or isinstance(b, Tensor)

    # Get all function arguments as non-tensors (i.e. either ints or arrays)
    arg_a = a.array if isinstance(a, Tensor) else a
    arg_b = b.array if isinstance(b, Tensor) else b

    array = arg_a * arg_b
    requires_grad = (a.requires_grad if isinstance(a, Tensor) else False)
    requires_grad = requires_grad or (b.requires_grad if isinstance(b, Tensor) else False)
    requires_grad = requires_grad and grad_tracking_enabled
    
    ret = Tensor(array, requires_grad)

    if not requires_grad:
        return ret
    
    parents = {}

    if isinstance(a, Tensor):
        parents[0] = a
    
    if isinstance(b, Tensor):
        parents[1] = b

    ret.recipe = Recipe(
        np.multiply,
        (arg_a, arg_b),
        {},
        parents
    )

    return ret


multiply = multiply_forward
tests.test_multiply(Tensor, multiply_forward)
tests.test_multiply_no_grad(Tensor, multiply_forward)
tests.test_multiply_float(Tensor, multiply_forward)
a = Tensor([2], requires_grad=True)
b = Tensor([3], requires_grad=True)
grad_tracking_enabled = False
b = multiply_forward(a, b)
grad_tracking_enabled = True
assert not b.requires_grad, "should not require grad if grad tracking globally disabled"
assert b.recipe is None, "should not create recipe if grad tracking globally disabled"

All tests in `test_multiply` passed!
All tests in `test_multiply_no_grad` passed!
All tests in `test_multiply_float` passed!


<details>
<summary>Help - I get <code>AttributeError: 'int' object has no attribute 'array'</code>.</summary>

Remember that your multiply function should also accept integers. You need to separately deal with the cases where `a` and `b` are integers or Tensors.
</details>

<details>
<summary>Help - I get <code>AssertionError: assert len(c.recipe.parents) == 1 and c.recipe.parents[0] is a</code> in the "test_multiply_float" test.</summary>

This is probably because you've stored the inputs to `multiply` as integers when one of the is an integer. Remember, `parents` should just be a list of the **Tensors** that were inputs to `multiply`, so you shouldn't add ints.
</details>


<details><summary>Solution</summary>

```python
def multiply_forward(a: Tensor | int, b: Tensor | int) -> Tensor:
    """Performs np.multiply on a Tensor object."""
    assert isinstance(a, Tensor) or isinstance(b, Tensor)

    # Get all function arguments as non-tensors (i.e. either ints or arrays)
    arg_a = a.array if isinstance(a, Tensor) else a
    arg_b = b.array if isinstance(b, Tensor) else b

    # Calculate the output (which is a numpy array)
    out_arr = arg_a * arg_b
    assert isinstance(out_arr, np.ndarray)

    # Find whether the tensor requires grad (need to check if ANY of the inputs do)
    requires_grad = grad_tracking_enabled and any(
        [isinstance(x, Tensor) and x.requires_grad for x in (a, b)]
    )

    # Create the output tensor from the underlying data and the requires_grad flag
    out = Tensor(out_arr, requires_grad)

    # If requires_grad, then create a recipe
    if requires_grad:
        parents = {idx: arr for idx, arr in enumerate([a, b]) if isinstance(arr, Tensor)}
        out.recipe = Recipe(np.multiply, (arg_a, arg_b), {}, parents)

    return out
```
</details>

## Forward Pass - Generic Version

All our forward functions are going to look extremely similar to `log_forward` and `multiply_forward`.
Implement the higher order function `wrap_forward_fn` that takes a `Arr -> Arr` function and returns a `Tensor -> Tensor` function. In other words, `wrap_forward_fn(np.multiply)` should evaluate to a callable that does the same thing as your `multiply_forward` (and same for `np.log`).

### Exercise - implement `wrap_forward_fn`

> ```yaml
> Difficulty: 🔴🔴🔴🔴⚪
> Importance: 🔵🔵🔵🔵⚪
> 
> You should spend up to 20-25 minutes on this exercise.
> This exercise is probably the 2nd most conceptually important today, after the backprop implementation at the end of the section.
> ```

If you're stuck, you can start with the same structure as the wrapped multiply function above (i.e. just copy and paste the code from solutions and use this as a stand in for `tensor_func` below, then modify it).

In [12]:
def wrap_forward_fn(numpy_func: Callable, is_differentiable=True) -> Callable:
    """
    Args:
        numpy_func:
            takes any number of positional arguments, some of which may be NumPy arrays, and any
            number of keyword arguments which we aren't allowing to be NumPy arrays at present. It
            returns a single NumPy array.

        is_differentiable:
            if True, numpy_func is differentiable with respect to some input argument, so we may
            need to track information in a Recipe. If False, we definitely don't need to track
            information.

    Returns:
        tensor_func
            It has the same signature as numpy_func, except it operates on Tensors instead of Arr.
    """

    def tensor_func(*args: Any, **kwargs: Any) -> Tensor:
        # Get all function arguments as non-tensors (i.e. either ints or arrays)
        arg_arrays = tuple([(a.array if isinstance(a, Tensor) else a) for a in args])

        # YOUR CODE HERE - create output array & make it a tensor with requires_grad (& recipe)
        
        # print(arg_arrays, kwargs)
        out_array = numpy_func(*arg_arrays, **kwargs)
        # print(out_array)
        if not grad_tracking_enabled or not is_differentiable:
            return Tensor(out_array, False)
        
        requires_grad = False
        parents = {}
        for i, arg in enumerate(args):
            if not isinstance(arg, Tensor):
                continue

            parents[i] = arg

            if arg.requires_grad:
                requires_grad = True

        if not requires_grad:
            return Tensor(out_array, False)
        
        out = Tensor(out_array, True)

        out.recipe = Recipe(
            numpy_func,
            arg_arrays,
            kwargs,
            parents
        )

        return out

    return tensor_func


def _sum(x: Arr, dim=None, keepdim=False) -> Arr:
    # need to be careful with sum, because kwargs have different names in torch and numpy
    return np.sum(x, axis=dim, keepdims=keepdim)


log = wrap_forward_fn(np.log)
multiply = wrap_forward_fn(np.multiply)
eq = wrap_forward_fn(np.equal, is_differentiable=False)
sum = wrap_forward_fn(_sum)

tests.test_log(Tensor, log)
tests.test_log_no_grad(Tensor, log)
tests.test_multiply(Tensor, multiply)
tests.test_multiply_no_grad(Tensor, multiply)
tests.test_multiply_float(Tensor, multiply)
tests.test_eq(Tensor, eq)
tests.test_sum(Tensor)

All tests in `test_log` passed!
All tests in `test_log_no_grad` passed!
All tests in `test_multiply` passed!
All tests in `test_multiply_no_grad` passed!
All tests in `test_multiply_float` passed!
All tests in `test_eq` passed!
All tests in `test_sum` passed!


<details>
<summary>Help - I'm getting <code>NameError: name 'getitem' is not defined</code>.</summary>

This is probably because you're calling `numpy_func` on the args themselves. Recall that `args` will be a list of `Tensor` objects, and that you should call `numpy_func` on the underlying arrays.
</details>

<details>
<summary>Help - I'm getting an AssertionError on <code>assert c.requires_grad == True</code> (or something similar).</summary>

This is probably because you're not defining `requires_grad` correctly. Remember that the output of a forward function should have `requires_grad = True` if and only if all of the following hold:

* Grad tracking is enabled
* The function is differentiable
* **Any** of the inputs are tensors with `requires_grad = True`
</details>

<details>
<summary>Help - my function passes all tests up to <code>test_sum</code>, but then fails here.</summary>

`test_sum`, unlike the previous tests, wraps a function that uses keyword arguments. So if you're failing here, it's probably because you didn't use `kwargs` correctly.

`kwargs` should be used in two ways: once when actually calling the `numpy_func`, and once when defining the `Recipe` object for the output tensor.
</details>


<details><summary>Solution</summary>

```python
def wrap_forward_fn(numpy_func: Callable, is_differentiable=True) -> Callable:
    """
    Args:
        numpy_func:
            takes any number of positional arguments, some of which may be NumPy arrays, and any
            number of keyword arguments which we aren't allowing to be NumPy arrays at present. It
            returns a single NumPy array.

        is_differentiable:
            if True, numpy_func is differentiable with respect to some input argument, so we may
            need to track information in a Recipe. If False, we definitely don't need to track
            information.

    Returns:
        tensor_func
            It has the same signature as numpy_func, except it operates on Tensors instead of Arr.
    """

    def tensor_func(*args: Any, **kwargs: Any) -> Tensor:
        # Get all function arguments as non-tensors (i.e. either ints or arrays)
        arg_arrays = tuple([(a.array if isinstance(a, Tensor) else a) for a in args])

        # Calculate the output (which is a numpy array)
        out_arr = numpy_func(*arg_arrays, **kwargs)

        # Find whether the tensor requires grad (need to check if ANY of the inputs do)
        requires_grad = (
            grad_tracking_enabled
            and is_differentiable
            and any([(isinstance(a, Tensor) and a.requires_grad) for a in args])
        )

        # Create the output tensor from the underlying data and the requires_grad flag
        out = Tensor(out_arr, requires_grad)

        # If requires_grad, then create a recipe
        if requires_grad:
            parents = {idx: a for idx, a in enumerate(args) if isinstance(a, Tensor)}
            out.recipe = Recipe(numpy_func, arg_arrays, kwargs, parents)

        return out

    return tensor_func
```
</details>

Note - none of these functions involve keyword args, so the tests won't detect if you're handling kwargs incorrectly (or even failing to use them at all). If your code fails in later exercises, you might want to come back here and check that you're using the kwargs correctly. Alternatively, once you pass the tests, you can compare your code to the solutions and see how they handle kwargs.

## Backpropagation

Now all the pieces are in place to implement backpropagation. We need to loop over our nodes from right to left (i.e. starting with the tensors computed last and moving backwards chronologically). At each node, we:

- Call the backward function to transform the grad wrt output to the grad wrt input.
- If the node is a leaf, write the grad to the grad field.
- Otherwise, accumulate the grad into temporary storage.

### Topological Sort

As part of backprop, we need to sort the nodes of our graph so we can traverse the graph in the appropriate order.

### Exercise - implement `topological_sort`

> ```yaml
> Difficulty: 🔴🔴🔴🔴⚪
> Importance: 🔵⚪⚪⚪⚪
> 
> You should spend up to 20-25 minutes on this exercise.
> Note, it's completely fine to skip this problem if you're not very interested in it.
> It's more of a fun LeetCode-style challenge, and writing a solution for it isn't crucial for understanding today's content.
> ```

Write a general function `topological_sort` that return a list of node's children in topological order (beginning with the furthest descendants, ending with the starting node) using [depth-first search](https://en.wikipedia.org/wiki/Topological_sorting).

We've given you a `Node` class, with a `children` attribute, and a `get_children` function. You shouldn't change any of these, and your `topological_sort` function should use `get_children` to access a node's children rather than calling `node.children` directly. In subsequent exercises, we'll replace the `Node` class with the `Tensor` class (and using a different `get_children` function), so this will ensure your code still works for this new case.

If you're stuck, try looking at the pseudocode from some of [these examples](https://en.wikipedia.org/wiki/Topological_sorting#Kahn's_algorithm).

In [13]:
class Node:
    def __init__(self, *children):
        self.children = list(children)


def get_children(node: Node) -> list[Node]:
    return node.children


def topological_sort(node: Node, get_children: Callable) -> list[Node]:
    """
    Return a list of node's descendants in reverse topological order from future
    to past (i.e. `node` should be last).

    Should raise an error if the graph with `node` as root is not in fact acyclic.
    """
    result: list[
        Node
    ] = []  # stores the list of nodes to be returned (in reverse topological order)
    perm: set[Node] = set()  # same as `result`, but as a set (faster to check for membership)
    temp: set[Node] = set()  # keeps track of previously visited nodes (to detect cyclicity)

    def visit(cur: Node):
        """
        Recursive function which visits all the children of the current node,
        and appends them all to `result` in the order they were found.
        """
        if cur in perm:
            return
        if cur in temp:
            raise ValueError("Not a DAG!")
        temp.add(cur)

        for next in get_children(cur):
            visit(next)

        result.append(cur)
        perm.add(cur)
        temp.remove(cur)

    visit(node)
    return result


tests.test_topological_sort_linked_list(topological_sort)
tests.test_topological_sort_branching(topological_sort)
tests.test_topological_sort_rejoining(topological_sort)
tests.test_topological_sort_cyclic(topological_sort)

All tests in `test_topological_sort_linked_list` passed!
All tests in `test_topological_sort_branching` passed!
All tests in `test_topological_sort_rejoining` passed!
All tests in `test_topological_sort_cyclic` passed!


<details>
<summary>Help - my function is hanging without returning any values.</summary>

This is probably because it's going around in cycles when fed a cyclic graph. You should add a way of raising an error if your function detects that the graph isn't cyclic. One way to do this is to create a set `temp`, which stores the nodes you've visited on a particular excursion into the graph, then you can raise an error if you come across an already visited node.
</details>

<details>
<summary>Help - I'm completely stuck on how to implement this, and would like the template for some code.</summary>

Here is the template for a depth-first search implementation:

```python
def topological_sort(node: Node, get_children: Callable) -> list[Node]:
    
    result: list[Node] = [] # stores the list of nodes to be returned (in reverse topological order)
    perm: set[Node] = set() # same as `result`, but as a set (faster to check for membership)
    temp: set[Node] = set() # keeps track of previously visited nodes (to detect cyclicity)

    def visit(cur: Node):
        '''
        Recursive function which visits all the children of the current node, and appends them all
        to `result` in the order they were found.
        '''
        pass

    visit(node)
    return result
```
</details>


<details><summary>Solution</summary>

```python
def topological_sort(node: Node, get_children: Callable) -> list[Node]:
    """
    Return a list of node's descendants in reverse topological order from future
    to past (i.e. `node` should be last).

    Should raise an error if the graph with `node` as root is not in fact acyclic.
    """
    result: list[
        Node
    ] = []  # stores the list of nodes to be returned (in reverse topological order)
    perm: set[Node] = set()  # same as `result`, but as a set (faster to check for membership)
    temp: set[Node] = set()  # keeps track of previously visited nodes (to detect cyclicity)

    def visit(cur: Node):
        """
        Recursive function which visits all the children of the current node,
        and appends them all to `result` in the order they were found.
        """
        if cur in perm:
            return
        if cur in temp:
            raise ValueError("Not a DAG!")
        temp.add(cur)

        for next in get_children(cur):
            visit(next)

        result.append(cur)
        perm.add(cur)
        temp.remove(cur)

    visit(node)
    return result
```
</details>

Now, we've given you the function `sorted_computational_graph`. This calls `topological_sort` and returns the result in reverse order (because we want to start with the root node). The "get children" function we're using here is "return all tensors in the recipe for this tensor".

<img src="https://github.com/callummcdougall/Fundamentals/blob/main/images/abcdefg.png?raw=true" width=500>

In [14]:
def sorted_computational_graph(tensor: Tensor) -> list[Tensor]:
    """
    For a given tensor, return a list of Tensors that make up the nodes of the given Tensor's
    computational graph, in reverse topological order (i.e. `tensor` should be first).
    """

    def get_parents(tensor: Tensor) -> list[Tensor]:
        if tensor.recipe is None:
            return []
        return list(tensor.recipe.parents.values())

    return topological_sort(tensor, get_parents)[::-1]


a = Tensor([1], requires_grad=True)
b = Tensor([2], requires_grad=True)
c = Tensor([3], requires_grad=True)
d = a * b
e = c.log()
f = d * e
g = f.log()
name_lookup = {a: "a", b: "b", c: "c", d: "d", e: "e", f: "f", g: "g"}

print([name_lookup[t] for t in sorted_computational_graph(g)])

['g', 'f', 'e', 'c', 'd', 'b', 'a']


Compare your output with the computational graph. You should never be printing `x` before `y` if there is an edge `x --> ... --> y` (this should result in approximately reverse alphabetical order).

### The `backward` method

Now we're really ready for backprop!

Recall that in the implementation of the class `Tensor`, we had:

```python
class Tensor:
    ...
    def backward(self, end_grad: "Arr | Tensor | None" = None) -> None:
        if isinstance(end_grad, Arr):
            end_grad = Tensor(end_grad)
        return backprop(self, end_grad)
```

In other words, for a tensor `out`, calling `out.backward()` is equivalent to `backprop(out)`.

Recall that in the last section, we said that calling `backward` on a scalar tensor is equivalent to backpropagating on the weighted sum of all the elements of the tensor, i.e. `L = (tensor * v).sum()`. By default `v` is a tensor of 1s of the same shape as the tensor you're calling `backward` from, meaning we're just backpropagating on `L.sum()`. Here, the `end_grad` argument you pass to `backward` gives you the option to override this default behaviour, in other words if it's supplied you should use it as the first input to your backward function instead of a tensor of 1s. The use case for this is pretty niche (used for things like **influence functions**), but it's still useful to understand!

### Exercise - implement `backprop`

> ```yaml
> Difficulty: 🔴🔴🔴🔴🔴
> Importance: 🔵🔵🔵🔵🔵
> 
> You should spend up to 30-45 minutes on this exercise.
> 
> This exercise is the most conceptually important today, and probably the hardest. We've provided several dropdowns to help you.
> ```

Now, we get to the actual backprop function! Some code is provided below, which you should complete.

If you want a challenge, you can try and implement it straight away, with out any help. However, because this is quite a challenging exercise, you can also use the dropdowns below. The first one gives you a sketch of the backpropagation algorithm, the second gives you a diagram which provides a bit more detail, and the third gives you the annotations for the function (so you just have to fill in the code). You are recommended to start by trying to implement it without help, but use the dropdowns (in order) if this is too difficult.

We've also provided a few dropdowns to address specific technical errors that can arise from implementing this function. If you're having trouble, you can use these to help you debug. You should take some time with this function, as it's definitely the most important exercise to understand today.

In [15]:
def backprop(end_node: Tensor, end_grad: Tensor | None = None) -> None:
    """Accumulates gradients in the grad field of each leaf node.

    tensor.backward() is equivalent to backprop(tensor).

    end_node:
        The rightmost node in the computation graph. If it contains more than one element, end_grad
        must be provided.
    end_grad:
        A tensor of the same shape as end_node. Set to 1 if not specified and end_node has only one
        element.
    """
    # Get value of end_grad_arr
    end_grad_arr = np.ones_like(end_node.array) if end_grad is None else end_grad.array

    # Create dict to store gradients
    grads: dict[Tensor, Arr] = {end_node: end_grad_arr}

    # YOUR CODE HERE - iterate through the sorted computational graph, performing backprop algorithm
    processing_order: list[Tensor] = sorted_computational_graph(end_node)
    for node in processing_order:
        out_grad = grads.pop(node)

        if node.is_leaf:
            if node.requires_grad:
                node.grad = Tensor(out_grad) if node.grad is None else node.grad + out_grad
        else :
            for pos, parent in node.recipe.parents.items():
                back_fn = BACK_FUNCS.get_back_func(node.recipe.func, pos)
                grad = back_fn(out_grad, node.array, *node.recipe.args, **node.recipe.kwargs)
                grads[parent] = grad if (parent not in grads) else grads[parent] + grad


tests.test_backprop(Tensor)
tests.test_backprop_branching(Tensor)
tests.test_backprop_requires_grad_sum(Tensor)
tests.test_backprop_requires_grad_false(Tensor)
tests.test_backprop_float_arg(Tensor)

All tests in `test_backprop` passed!
All tests in `test_backprop_branching` passed!
All tests in `test_backprop_requires_grad_sum` passed!
All tests in `test_backprop_requires_grad_false` passed!
All tests in `test_backprop_float_arg` passed!


<details>
<summary>Help - I get AttributeError: 'NoneType' object has no attribute 'func'</summary>

This error is probably because you're trying to access `recipe.func` from the wrong node. Possibly, you're calling your backward functions using the parents nodes' `recipe.func`, rather than the node's `recipe.func`.
        
To explain further, suppose your computational graph is simply:

<img src="https://raw.githubusercontent.com/info-arena/ARENA_img/refs/heads/main/img/Screenshot%25202023-02-17%2520174308.png" width=320>

When you reach `b` in your backprop iteration, you should calculate the gradient wrt `a` (the only parent of `b`) and store it in your `grads` dictionary, as `grads[a]`. In order to do this, you need the backward function for `func1`, which is stored in the node `b` (recall that the recipe of a tensor can be thought of as a set of instructions for how that tensor was created).
</details>

<details>
<summary>Help - I get AttributeError: 'numpy.ndarray' object has no attribute 'array'</summary>

This might be because you've set `node.grad` to be an array, rather than a tensor. You should store gradients as tensors (think of PyTorch, where `tensor.grad` will have type `torch.Tensor`).
        
It's fine to store numpy arrays in the `grads` dictionary, but when it comes time to set a tensor's grad attribute, you should use a tensor.
</details>

<details>
<summary>Help - I get 'RuntimeError: bool value of Tensor with more than one value is ambiguous'.</summary>

This error is probably because your computational graph function checks whether a tensor is in a list. The way these classes are compared for equality is a bit funky, and using sets rather than lists should make this error go away (i.e. checking whether a tensor is in a set should be fine).
</details>

<details>
<summary>Help - I'm failing on the <code>test_backprop_requires_grad_sum</code> test and I don't know why.</summary>

This test is designed to spot cases where you're accidentally **overwriting the gradient with each backward fn call**, rather than summing them. Remember that if a node has multiple paths from itself to the end node, then that node's grad attribute should be the sum of the gradients from all those

</details>

<details>
<summary>Help - I'm stuck, and I need a template for the function.</summary>

You just need to fill in the code below the comments labelled (1) and (2).

```python
def backprop(end_node: Tensor, end_grad: Tensor | None = None) -> None:

    # Get value of end_grad_arr
    end_grad_arr = np.ones_like(end_node.array) if end_grad is None else end_grad.array

    # Create dict to store gradients
    grads: dict[Tensor, Arr] = {end_node: end_grad_arr}

    for node in sorted_computational_graph(end_node):
        outgrad = grads.pop(node)

        # (1) If this is a leaf node, then set/update the gradient if requires_grad
        ...

        # (2) If this isn't a leaf node, then iterate through this node's parents and update their values in the `grads`
        # dict, using the outgrad values returned from this node's backward function
        ...
```

</details>


<details><summary>Solution</summary>

```python
def backprop(end_node: Tensor, end_grad: Tensor | None = None) -> None:
    """Accumulates gradients in the grad field of each leaf node.

    tensor.backward() is equivalent to backprop(tensor).

    end_node:
        The rightmost node in the computation graph. If it contains more than one element, end_grad
        must be provided.
    end_grad:
        A tensor of the same shape as end_node. Set to 1 if not specified and end_node has only one
        element.
    """
    # Get value of end_grad_arr
    end_grad_arr = np.ones_like(end_node.array) if end_grad is None else end_grad.array

    # Create dict to store gradients
    grads: dict[Tensor, Arr] = {end_node: end_grad_arr}

    for node in sorted_computational_graph(end_node):
        # Get the outgrad from the grads dict
        outgrad = grads.pop(node)

        # (1) If it's a leaf node, then set/update gradient if requires_grad=True, and stop here.
        if node.is_leaf:
            if node.requires_grad:
                node.grad = Tensor(outgrad) if node.grad is None else node.grad + outgrad

        # (2) If not a leaf node then it must have a recipe, so we iterate through its parents and
        # update their grads.
        else:
            for argnum, parent in node.recipe.parents.items():
                # Get backward function, from the fwd function that created `node` from `parent`.
                back_fn = BACK_FUNCS.get_back_func(node.recipe.func, argnum)

                # Use it to compute the gradient we'll add onto parent from the path `parent -> node
                # -> ... -> end_node`.
                in_grad = back_fn(outgrad, node.array, *node.recipe.args, **node.recipe.kwargs)

                # Add this gradient to the grads dict (handling special case where parent is not in
                # grads yet).
                grads[parent] = in_grad if (parent not in grads) else grads[parent] + in_grad
```
</details>

# 3️⃣ Training on MNIST from scratch

> ##### Learning Objectives
>
> * Implement more forward and backward functions, including for indexing, summing, and matrix multiplication
> * Learn how to build higher-level abstractions like parameters and modules on top of individual functions and tensors
> * Complete the process of building up a neural network from scratch and training it via gradient descent.

Congrats on implementing backprop! Soon we'll be able to train a full model from scratch, but first we'll go through a bunch of backward functions which will be necessary for training (as well as ones that cover some interesting cases). These should be a lot like your `log_back` and `multiply_back0`, `multiplyback1` examples earlier.

## More backward functions!

> Note - some of these exercises can get a bit repetitive, and so **you're welcome to skip through many of these exercises if you don't find them interesting, and/or you're pressed for time.** The exercises in the section "Parameters & Modules" and beyond are much more conceptually valuable.
> 
> Additionally, most of these functions can be implemented simply in 1 or 2 lines, so if you find yourself writing a lot more than that then you might want to look at the solution instead.

### Exercise - `negative`

> ```yaml
> Difficulty: 🔴⚪⚪⚪⚪
> Importance: 🔵⚪⚪⚪⚪
> 
> You should spend up to ~5 minutes on this exercise (it's not a trick question, it is as simple as it looks!).
> ```

`torch.negative` just performs `-x` elementwise. Make your own version `negative` using `wrap_forward_fn`. Note, you don't need to worry about unbroadcasting here because `np.negative` won't change the input shape (technically it can since `np.negative(x, out)` is actually the negative version of `x` broadcasted to the shape of `out`, but we won't be using it in this way during our exercises).

In [16]:
def negative_back(grad_out: Arr, out: Arr, x: Arr) -> Arr:
    """Backward function for f(x) = -x elementwise."""
    return grad_out * -1


negative = wrap_forward_fn(np.negative)
BACK_FUNCS.add_back_func(np.negative, 0, negative_back)

tests.test_negative_back(Tensor)

All tests in `test_negative_back` passed!


<details><summary>Solution</summary>

```python
def negative_back(grad_out: Arr, out: Arr, x: Arr) -> Arr:
    """Backward function for f(x) = -x elementwise."""
    return -grad_out
```
</details>

### Exercise - `exp`

> ```yaml
> Difficulty: 🔴⚪⚪⚪⚪
> Importance: 🔵🔵⚪⚪⚪
> 
> You should spend up to 5-10 minutes on this exercise.
> ```

Make your own version of `torch.exp`. The backward function should express the result in terms of the `out` parameter - this more efficient than expressing it in terms of `x`.

In [17]:
def exp_back(grad_out: Arr, out: Arr, x: Arr) -> Arr:
    """Backward function for f(x) = exp(x) elementwise."""
    return grad_out * out


exp = wrap_forward_fn(np.exp)
BACK_FUNCS.add_back_func(np.exp, 0, exp_back)

tests.test_exp_back(Tensor)

All tests in `test_exp_back` passed!


<details><summary>Solution</summary>

```python
def exp_back(grad_out: Arr, out: Arr, x: Arr) -> Arr:
    """Backward function for f(x) = exp(x) elementwise."""
    return out * grad_out
```
</details>

### Exercise - `reshape`

> ```yaml
> Difficulty: 🔴🔴⚪⚪⚪
> Importance: 🔵⚪⚪⚪⚪
> 
> You should spend up to 5-10 minutes on this exercise.
> ```

`reshape` is a bit different than the functions we've dealt with so far: it changes the shape of the tensor, not its values. In other words, the backward function needs to be able to map from the gradient $\partial L / \partial \mathbf{x_r}$ to $\partial L / \partial \mathbf{x}$, where $\mathbf{x_r}$ is the reshaped version of $\mathbf{x}$.

Depending how you wrote `wrap_forward_fn` and `backprop`, you might need to go back and adjust them to handle this - if you're failing tests but think your implementation is correct, we recommend you go back to these functions and check them.

This function should just be a single line.

In [18]:
def reshape_back(grad_out: Arr, out: Arr, x: Arr, new_shape: tuple) -> Arr:
    """Backward function for torch.reshape."""
    return np.reshape(grad_out, x.shape)


reshape = wrap_forward_fn(np.reshape)
BACK_FUNCS.add_back_func(np.reshape, 0, reshape_back)

tests.test_reshape_back(Tensor)

All tests in `test_reshape_back` passed!


<details>
<summary>Solution (and explanation)</summary>

Explanation: the reshape operation that takes us from the tensor $\frac{\partial L}{\partial \mathbf{x_r}}$ to $\frac{\partial L}{\partial \mathbf{x}}$ is exactly the inverse of the forward reshape operation that produced $\mathbf{x_r}$ from $\mathbf{x}$. In other words, we want to to take `grad_out` and reshape it back to the shape of `x`.

```python
def reshape_back(grad_out: Arr, out: Arr, x: Arr, new_shape: tuple) -> Arr:
    """Backward function for torch.reshape."""
    return np.reshape(grad_out, x.shape)
```

</details>

### Exercise - `permute`

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵⚪⚪⚪⚪
> 
> You should spend up to 5-10 minutes on this exercise.
> ```

In NumPy, the equivalent of `torch.permute` is called `np.transpose`, so we will wrap that. Permute is somewhat similar to reshape, but the difference is that it does actually change the order of elements in the underlying array.

Hint - just like with `reshape`, the inverse of a transposition is another transposition. You might find the function `np.argsort` useful for getting the inverse transposition.

This function should also just be a single line.

In [19]:
def permute_back(grad_out: Arr, out: Arr, x: Arr, axes: tuple) -> Arr:
    """
    Backward function for torch.permute. Works by inverting the transposition in the forward
    function.
    """
    return np.transpose(grad_out, np.argsort(axes))


BACK_FUNCS.add_back_func(np.transpose, 0, permute_back)
permute = wrap_forward_fn(np.transpose)

tests.test_permute_back(Tensor)

All tests in `test_permute_back` passed!


<details>
<summary>Solution (and explanation)</summary>

The inverse of transposing with `axes` is transposing using `np.argsort(axes)`. To see this: the forward transpose will send axis `j` to axis `axes[j]`, and so we want the inverse transposition `axes_inv` to satisfy `axes_inv[axes[j]] = j`, in other words **the indices of `axes_inv` should sort `axes`** - this is exactly what `np.argsort` does.

```python
def permute_back(grad_out: Arr, out: Arr, x: Arr, axes: tuple) -> Arr:
    """
    Backward function for torch.permute. Works by inverting the transposition in the forward
    function.
    """
    return np.transpose(grad_out, np.argsort(axes))
```

</details>

### Exercise - `sum`

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵⚪⚪⚪
> 
> You should spend up to 20-30 minutes on this exercise.
> ```

The output can also be smaller than the input, such as when calling `torch.sum`.

Recall that when we looked at broadcasting, the backwards operation was summing over the broadcasted dimensions. This is because a broadcast operation effectively copies our tensor, giving it more gradient paths that we need to sum over. Similarly, the backwards operation for summing is broadcasting. We can intuitively see this as follows: if we have some value `L = L(x_summed)` where `x_summed` is the result of summing `x` over some number of dimensions, then editing `x_summed[i, j, ...] += delta` has the same downstream effect as editing any one of the `x` values which were summed over to get `x_summed[i, j, ...]`. So to get the gradient of `L` wrt `x`, we need to copy (broadcast) the gradient of `L` wrt `x_summed` up to the full size of `x`.

Implementing `sum_back` should have 2 steps:

1. **Adding new dims if they were summed over with `keepdim=False`**. You can do this with `np.expand_dims`, for example if `arr` has shape `(2, 3)` then `np.expand_dims(arr, (0, 2))` has shape `(1, 2, 1, 3)`, i.e. it's a new tensor with dummy dimensions created at indices 0 and 2.
2. **Broadcasting along dims that were summed over**. Since after step (1) you've effectively reduced to the `keepdim=True` case, you can now use `np.broadcast_to` to get the correct shape.

Note, if you get weird errors that you can't explain, and these exceptions don't even go away when you use the solutions provided, this could mean that your implementation of `wrap_forward_fn` was wrong in a way which wasn't picked up by the tests. You should return to this function and try to fix it (or just use the solution).

In [20]:
def sum_back(grad_out: Arr, out: Arr, x: Arr, dim=None, keepdim=False):
    """Backward function for torch.sum"""
    
    # print(f"\nx.shape: {x.shape} \t x:{x} \ndim: {dim} \nkeepdim: {keepdim}")
    # print(f"out.shape: {out.shape} \t  out: {out}")
    
    if (not keepdim) and (dim is not None):
        grad_out = np.expand_dims(grad_out, dim)
    
    # print(f"out.shape: {out.shape} \t  out: {out}")
    
    grad_out = np.broadcast_to(grad_out, x.shape)
    # print(f"out.shape: {out.shape} \t  out: {out}")
    
    # print("grad_out:", grad_out)
    # print("ret:", grad_out * out)
    return grad_out 


def _sum(x: Arr, dim=None, keepdim=False) -> Arr:
    """Like torch.sum, calling np.sum internally."""
    return np.sum(x, axis=dim, keepdims=keepdim)


sum = wrap_forward_fn(_sum)
BACK_FUNCS.add_back_func(_sum, 0, sum_back)

tests.test_sum_keepdim_false(Tensor)
tests.test_sum_keepdim_true(Tensor)
tests.test_sum_dim_none(Tensor)
tests.test_sum_nonscalar_grad_out(Tensor)

All tests in `test_sum_keepdim_false` passed!
All tests in `test_sum_keepdim_true` passed!
All tests in `test_sum_dim_none` passed!
All tests in `test_sum_nonscalar_grad_out` passed!


<details>
<summary>Help - I'm not sure how to handle the case where <code>dim=None</code>.</summary>

You can actually handle this pretty easily - if `dim=None` then `grad_out` will be a scalar, so it's always fine to broadcast it along the dims that were summed over! This means you can skip step (1), i.e. this step only needs to handle the case where `keepdim=False` and `dim` is not `None`.

</details>

<details>
<summary>Help - I get the error "Encountered error when running `backward` in the test for nonscalar grad_out."</summary>

This error is likely due to the fact that you're expanding your tensor in a way that doesn't refer to the dimensions being summed over (i.e. the `dim` argument).

Remember that in the previous exercise we assumed that the tensors were broadcastable with each other, and our functions could just internally call `np.broadcast_to` as a result. But here, one tensor is the sum over another tensor's dimensions, and if `keepdim=False` then they might not broadcast. For instance, if `x.shape = (2, 5)`, `out = x.sum(dim=1)` has shape `(2,)` and `grad_out.shape = (2,)`, then the tensors `grad_out` and `x` are not broadcastable.

How can you carefully handle the case where `keepdim=False` and `dim` doesn't just refer to dimensions at the start of the tensor? (Hint - try and use `np.expand_dims`).

</details>


<details><summary>Solution</summary>

```python
def sum_back(grad_out: Arr, out: Arr, x: Arr, dim=None, keepdim=False):
    """Backward function for torch.sum"""
    # Step (1): if keepdim=False, then we need to add back in dims, so grad_out and x have the
    # same number of dims. We don't bother with the dim=None case, since then grad_out is a scalar
    # and this will be handled by our broadcasting in step (2).
    if (not keepdim) and (dim is not None):
        grad_out = np.expand_dims(grad_out, dim)

    # Step (2): repeat grad_out along the dims over which x was summed
    return np.broadcast_to(grad_out, x.shape)
```
</details>

### Elementwise add, subtract, divide

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵⚪⚪⚪
> 
> You should spend up to 10-15 minutes on this exercise.
> ```

These are exactly analogous to the multiply case. Note that Python and NumPy have the notion of "floor division", which is a truncating integer division as in `7 // 3 = 2`. You can ignore floor division: - we only need the usual floating point division which is called "true division".

Use lambda functions to define and register the backward functions each in one line. We've given you the first one.

In [21]:
add = wrap_forward_fn(np.add)
subtract = wrap_forward_fn(np.subtract)
true_divide = wrap_forward_fn(np.true_divide)

BACK_FUNCS.add_back_func(np.add, 0, lambda grad_out, out, x, y: unbroadcast(grad_out, x))
# YOUR CODE HERE - continue adding to BACK_FUNCS, for each of the 3 functions & both arg orders
BACK_FUNCS.add_back_func(np.add, 1, lambda grad_out, out, x, y: unbroadcast(grad_out, y))
BACK_FUNCS.add_back_func(np.subtract, 0, lambda grad_out, out, x, y: unbroadcast(grad_out, x))
BACK_FUNCS.add_back_func(np.subtract, 1, lambda grad_out, out, x, y: unbroadcast(-grad_out, y))
BACK_FUNCS.add_back_func(np.true_divide, 0, lambda grad_out, out, x, y: unbroadcast(grad_out / y, x))
BACK_FUNCS.add_back_func(np.true_divide, 1, lambda grad_out, out, x, y: unbroadcast(grad_out * -x/(y**2), y))

tests.test_add_broadcasted(Tensor)
tests.test_subtract_broadcasted(Tensor)
tests.test_truedivide_broadcasted(Tensor)

All tests in `test_add_broadcasted` passed!
All tests in `test_subtract_broadcasted` passed!
All tests in `test_truedivide_broadcasted` passed!


<details><summary>Solution</summary>

```python
BACK_FUNCS.add_back_func(np.add, 0, lambda grad_out, out, x, y: unbroadcast(grad_out, x))
BACK_FUNCS.add_back_func(np.add, 1, lambda grad_out, out, x, y: unbroadcast(grad_out, y))
BACK_FUNCS.add_back_func(np.subtract, 0, lambda grad_out, out, x, y: unbroadcast(grad_out, x))
BACK_FUNCS.add_back_func(np.subtract, 1, lambda grad_out, out, x, y: unbroadcast(-grad_out, y))
BACK_FUNCS.add_back_func(
    np.true_divide, 0, lambda grad_out, out, x, y: unbroadcast(grad_out / y, x)
)
BACK_FUNCS.add_back_func(
    np.true_divide, 1, lambda grad_out, out, x, y: unbroadcast(grad_out * (-x / y**2), y)
)
```
</details>

### Indexing

If we have the gradient of `L` wrt `x[index]`, what is the gradient of `L` wrt `x`? The answer is it'll be an array of zeros, filled in with the values of `dL/dx[index]` at the appropriate index positions. For example, if `x = [1, 2, 3]` and `L = x[0]`, then we trivially have `dL/dx[0] = 1`, and we can compute `dL/dx = [1, 0, 0]` in this way.

In its full generality, exactly how you can index a `torch.Tensor` is really complicated and there are quite a few cases to handle separately. Our implementation only handles 2 cases:

- The index is an integer or tuple of integers.
- The index is a tuple of (array or Tensor) representing coordinates. Each array is 1D and of equal length. Some coordinates may be repeated. This is [Integer array indexing](https://numpy.org/doc/stable/user/basics.indexing.html#integer-array-indexing).

This latter case is very important, because it describes how we index correct logprobs / probabilities. For example if we're training a classifier and we have tensors `logprobs.shape = (batch_size, n_classes)` and `targets.shape = (n_classes,)` then we index the correct logprobs using `logprobs[arange(batch_size), targets]` (note that the `arange` function has been given to you earlier, when we defined the `Tensor` class - it's a simple wrapper around `np.arange`).

In [22]:
Index = int | tuple[int, ...] | tuple[Arr] | tuple[Tensor]


def coerce_index(index: Index):
    """Helper function: converts array of tensors to array of numpy arrays."""
    if isinstance(index, tuple) and all(isinstance(i, Tensor) for i in index):
        return tuple([i.array for i in index])
    else:
        return index


def _getitem(x: Arr, index: Index) -> Arr:
    """Like x[index] when x is a torch.Tensor."""
    return x[coerce_index(index)]


def getitem_back(grad_out: Arr, out: Arr, x: Arr, index: Index):
    """
    Backwards function for _getitem.

    Hint: use np.add.at(a, indices, b)
    This function works just like a[indices] += b, except that it allows for repeated indices.
    """
    new_grad_out = np.full_like(x, 0)
    np.add.at(new_grad_out, coerce_index(index), grad_out)
    return new_grad_out


getitem = wrap_forward_fn(_getitem)
BACK_FUNCS.add_back_func(_getitem, 0, getitem_back)

### Non-Differentiable Functions

For functions like `torch.argmax` or `torch.eq`, there's no sensible way to define gradients with respect to the input tensor. For these, we will still use `wrap_forward_fn` because we still need to unbox the arguments and box the result, but by passing `is_differentiable=False` we can avoid doing any unnecessary computation.

We've given you this one as an example:

In [23]:
def _argmax(x: Arr, dim=None, keepdim=False):
    """Like torch.argmax."""
    result = np.argmax(x, axis=dim)
    if keepdim:
        return np.expand_dims(result, axis=([] if dim is None else dim))
    return result


argmax = wrap_forward_fn(_argmax, is_differentiable=False)

a = Tensor([1.0, 0.0, 3.0, 4.0], requires_grad=True)
b = a.argmax()
assert not b.requires_grad
assert b.recipe is None
assert b.item() == 3

### In-Place Operations

Supporting in-place operations introduces substantial complexity and generally doesn't help performance that much. The problem is that if any of the inputs used in the backward function have been modified in-place since the forward pass, then the backward function will incorrectly calculate using the modified version. PyTorch will warn you when this causes a problem with the error "RuntimeError: a leaf Variable that requires grad is being used in an in-place operation.".

Note - you don't have to fill anything in here; just run the cell. If you're curious, you can implement inplace operations as a bonus exercise at the end, but for now we just warn against inplace operations unless we specify otherwise.

In [24]:
def add_(x: Tensor, other: Tensor, alpha: float = 1.0) -> Tensor:
    """Like torch.add_. Compute x += other * alpha in-place and return tensor."""
    np.add(x.array, other.array * alpha, out=x.array)
    return x


def sub_(x: Tensor, other: Tensor, alpha: float = 1.0) -> Tensor:
    """Like torch.sub_. Compute x -= other * alpha in-place and return tensor."""
    np.subtract(x.array, other.array * alpha, out=x.array)
    return x


def safe_example():
    """This example should work properly."""
    a = Tensor([0.0, 1.0, 2.0, 3.0], requires_grad=True)
    b = Tensor([2.0, 3.0, 4.0, 5.0], requires_grad=True)
    a.add_(b)
    c = a * b
    c.sum().backward()
    assert a.grad is not None and np.allclose(a.grad.array, [2.0, 3.0, 4.0, 5.0])
    assert b.grad is not None and np.allclose(b.grad.array, [2.0, 4.0, 6.0, 8.0])


def unsafe_example():
    """
    This example is expected to compute the wrong gradients, because dc/db is calculated using the
    modified a.
    """
    a = Tensor([0.0, 1.0, 2.0, 3.0], requires_grad=True)
    b = Tensor([2.0, 3.0, 4.0, 5.0], requires_grad=True)
    c = a * b
    a.add_(b)
    c.sum().backward()
    if a.grad is not None and np.allclose(a.grad.array, [2.0, 3.0, 4.0, 5.0]):
        print("Grad wrt a is OK!")
    else:
        print("Grad wrt a is WRONG!")
    if b.grad is not None and np.allclose(b.grad.array, [0.0, 1.0, 2.0, 3.0]):
        print("Grad wrt b is OK!")
    else:
        print("Grad wrt b is WRONG!")


safe_example()
unsafe_example()

Grad wrt a is OK!
Grad wrt b is WRONG!


### Mixed Scalar-Tensor Operations

You may have been wondering why our `Tensor` class has to define both `__mul__` and `__rmul__` magic methods.

Without `__rmul__` defined, executing `2 * a` when `a` is a `Tensor` would try to call `2.__mul__(a)`, and the built-in class `int` would be confused about how to handle this.

Since we have defined `__rmul__` for you at the start, and you implemented multiply to work with floats as arguments, the following should "just work".

In [25]:
a = Tensor([0, 1, 2, 3], requires_grad=True)
(a * 2).sum().backward()
b = Tensor([0, 1, 2, 3], requires_grad=True)
(2 * b).sum().backward()
assert a.grad is not None
assert b.grad is not None
assert np.allclose(a.grad.array, b.grad.array)

### Exercise - `max`

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵⚪⚪⚪
> 
> You should spend up to 10-15 minutes on this exercise.
> ```

Since this is an elementwise function, we can think about the scalar case. For scalar $x$, $y$, the derivative for $\max(x, y)$ wrt $x$ is 1 when $x > y$ and 0 when $x < y$. What should happen when $x = y$?

Intuitively, since $\max(x, x)$ is equivalent to the identity function which has a derivative of 1 wrt $x$, it makes sense for the sum of our partial derivatives wrt $x$ and $y$ to also therefore total 1. The convention used by PyTorch is to split the derivative evenly between the two arguments. We will follow this behavior for compatibility, but it's just as legitimate to say it's 1 wrt $x$ and 0 wrt $y$, or some other arbitrary combination that sums to one.

<details>
<summary>Help - I'm not sure how to implement this function.</summary>

Try returning `grad_out * bool_sum`, where `bool_sum` is an array constructed from the sum of two boolean arrays.

You can alternatively use `np.where`.
</details>

<details>
<summary>Help - I'm passing the first test but not the second.</summary>

This probably means that you haven't implemented `unbroadcast`. You'll need to do this, to get `grad_out` into the right shape before you use it in `np.where`.
</details>

In [26]:
def maximum_back0(grad_out: Arr, out: Arr, x: Arr, y: Arr):
    """Backwards function for max(x, y) wrt x."""
    bool_sum = np.zeros(out.shape)
    bool_sum += 0.5 * (x == y)
    bool_sum += (x > y)
    return unbroadcast(grad_out * bool_sum, x)


def maximum_back1(grad_out: Arr, out: Arr, x: Arr, y: Arr):
    """Backwards function for max(x, y) wrt y."""
    bool_sum = np.zeros(out.shape)
    bool_sum += 0.5 * (x == y)
    bool_sum += (x < y)
    return unbroadcast(grad_out * bool_sum, y)


maximum = wrap_forward_fn(np.maximum)
BACK_FUNCS.add_back_func(np.maximum, 0, maximum_back0)
BACK_FUNCS.add_back_func(np.maximum, 1, maximum_back1)

tests.test_maximum(Tensor)
tests.test_maximum_broadcasted(Tensor)

All tests in `test_maximum` passed!
All tests in `test_maximum_broadcasted` passed!


<details><summary>Solution</summary>

```python
def maximum_back0(grad_out: Arr, out: Arr, x: Arr, y: Arr):
    """Backwards function for max(x, y) wrt x."""
    bool_sum = (x > y) + 0.5 * (x == y)
    return unbroadcast(grad_out * bool_sum, x)


def maximum_back1(grad_out: Arr, out: Arr, x: Arr, y: Arr):
    """Backwards function for max(x, y) wrt y."""
    bool_sum = (x < y) + 0.5 * (x == y)
    return unbroadcast(grad_out * bool_sum, y)
```
</details>

### Exercise - functional `ReLU`

> ```yaml
> Difficulty: 🔴⚪⚪⚪⚪
> Importance: 🔵⚪⚪⚪⚪
> 
> You should spend ~5 minutes on this exercise.
> ```

A simple and correct ReLU function can be defined in terms of your maximum function. Note the PyTorch version also supports in-place operation, which we are punting to the bonus section for now.

Again, at $x = 0$ your derivative could reasonably be anything between 0 and 1 inclusive, but we've followed PyTorch in making it 0.5. This means you can just use the `maximum` function defined above!

In [27]:
def relu(x: Tensor) -> Tensor:
    """Like torch.nn.function.relu(x, inplace=False)."""
    return maximum(x, 0.0)


tests.test_relu(Tensor)

All tests in `test_relu` passed!


<details><summary>Solution</summary>

```python
def relu(x: Tensor) -> Tensor:
    """Like torch.nn.function.relu(x, inplace=False)."""
    return maximum(x, 0.0)
```
</details>

### Exercise - 2D `matmul`

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵🔵⚪⚪
> 
> You should spend up to 20-25 minutes on this exercise.
> ```

Implement your version of `torch.matmul`, restricting it to the simpler case where both inputs are 2D (this means we don't need to worry about unbroadcasting or anything).

Note - althought the solution to this exercise is very short (just one line), you may find the actual mathematical derivation a bit tricky. We've given hints to help you, which we recommend using if you're stuck.

In [28]:
def _matmul2d(x: Arr, y: Arr) -> Arr:
    """Matrix multiply restricted to the case where both inputs are exactly 2D."""
    return x @ y


def matmul2d_back0(grad_out: Arr, out: Arr, x: Arr, y: Arr) -> Arr:
    return grad_out @ y.T

def matmul2d_back1(grad_out: Arr, out: Arr, x: Arr, y: Arr) -> Arr:
    return x.T @ grad_out


matmul = wrap_forward_fn(_matmul2d)
BACK_FUNCS.add_back_func(_matmul2d, 0, matmul2d_back0)
BACK_FUNCS.add_back_func(_matmul2d, 1, matmul2d_back1)

tests.test_matmul2d(Tensor)

All tests in `test_matmul2d` passed!


<details>
<summary>Help - I need a hint about the math</summary>

Let $X$, $Y$ and $M$ denote the variables `x`, `y` and `out`, so we have the matrix relation $M = XY$. The object `grad_out` is a tensor with elements `grad_out[p, q]` $ = \frac{\partial L}{\partial M_{p q}}$.

The output of `matmul2d_back0` should be the gradient of $L$ wrt $X$, i.e. it should have elements $\frac{\partial L}{\partial X_{i j}}$. Can you write this in terms of the elements of `x`, `y`, `out` and `grad_out`?
</details>

<details>
<summary>Help - I need the math explained</summary>

We can write $\frac{\partial L}{\partial X_{i j}}$ as:

$$
\begin{aligned}
\frac{\partial L}{\partial X_{i j}} &=\sum_{pq} \frac{\partial L}{\partial M_{p q}} \frac{\partial M_{p q}}{\partial X_{i j}} \\
&=\sum_{pqr} \left[\text{ grad\_out }\right]_{p q} \frac{\partial (X_{p r} Y_{r q})}{\partial X_{i j}} \\
&=\sum_{q} \left[\text{ grad\_out }\right]_{iq} Y_{j q} \\
&= \left[\text{ grad\_out } \times Y^{\top}\right]_{ij}
\end{aligned}
$$

where the second line follows because $M_{pq} = \sum_r X_{pr} Y_{rq}$ (and we can rearrange the summands), and the third line follows because $\frac{\partial{X_{pr}}}{X_{ij}} = 1 \text{ if } (p, r) = (i, j), \text{ else } 0$.


In other words, the `x.grad` attribute should be is `grad_out @ y.T`.

You can calculate the gradient wrt `y` in a similar way - we leave this as an exercise for the reader.
</details>


<details><summary>Solution</summary>

```python
def _matmul2d(x: Arr, y: Arr) -> Arr:
    """Matrix multiply restricted to the case where both inputs are exactly 2D."""
    return x @ y


def matmul2d_back0(grad_out: Arr, out: Arr, x: Arr, y: Arr) -> Arr:
    return grad_out @ y.T


def matmul2d_back1(grad_out: Arr, out: Arr, x: Arr, y: Arr) -> Arr:
    return x.T @ grad_out
```
</details>

## Parameters & Modules

We've now written enough backwards passes that we can go up a layer and write our own `nn.Parameter` and `nn.Module`. These are important abstractions that help us building up neural networks.

Below is a simple implementation of `Parameter`. It is itself a `Tensor`, shares storage with the provided `Tensor` and requires_grad is `True` by default - that's it! Make sure you understand the code being run in this cell to test the functionality of this class.

In [29]:
class Parameter(Tensor):
    def __init__(self, tensor: Tensor, requires_grad=True):
        """Share the array with the provided tensor."""
        return super().__init__(tensor.array, requires_grad=requires_grad)

    def __repr__(self):
        return f"Parameter containing:\n{super().__repr__()}"


x = Tensor([1.0, 2.0, 3.0])
p = Parameter(x)
assert p.requires_grad
assert p.array is x.array
assert (
    repr(p)
    == "Parameter containing:\nTensor(array([1., 2., 3.], dtype=float32), requires_grad=True)"
)
x.add_(Tensor(np.array(2.0)))
assert np.allclose(p.array, np.array([3.0, 4.0, 5.0])), (
    "in-place modifications to the original tensor should affect the parameter"
)

Just like `torch.Tensor`, the `nn.Module` class has a lot of functionality which we mostly don't care about today. We will just implement enough to get our network training.

Below is a simple implementation. We'll explain it a bit below (if you're already experienced in Python then this might be obvious to you and you can skip it).

- **Single-underscore attributes** are a notational convention; they're not treated differently by Python but they're used to indicate that the attribute is private and shouldn't be accessed directly by anyone using the class.
    - `_modules` is a dict mapping module names to module objects. The `modules` method returns an iterator over these modules.
    - `_parameters` is similar, with added recursion to include submodule parameters.
- **Double-underscore attributes** are special methods that determine how your class instance behaves when you use certain syntax.
    - `__call__` determines what the module does when you call it like a function. In this case, `module(*args, **kwargs)` calls `module.forward(**args, **kwargs)` - this is why we only ever need to implement `forward` in the modules we've written so far.
    - `__setattr__` manages attribute setting (i.e. running `module.attr = value` actually calls `module.__setattr__("attr", value)`). The default behaviour is to add the attribute to `self.__dict__`, but we've added custom logic so modules & parameters are also added to `self._modules` and `self._parameters` respectively - this is basically how logic like `module.parameters()` can work.
        - Note that there's a related method `__getattr__` which specifies attribute getting behaviour when lookup in `self.__dict__` fails.

In [30]:
class Module:
    _modules: dict[str, "Module"]
    _parameters: dict[str, Parameter]

    def __init__(self):
        self._modules: dict[str, "Module"] = {}
        self._parameters: dict[str, Parameter] = {}

    def modules(self) -> Iterator["Module"]:
        """Return the direct child modules of this module, not including self."""
        yield from self._modules.values()

    def parameters(self, recurse: bool = True) -> Iterator[Parameter]:
        """
        Return an iterator over Module parameters.

        recurse: if True, the iterator includes parameters of submodules, recursively.
        """
        yield from self._parameters.values()
        if recurse:
            for mod in self.modules():
                yield from mod.parameters(recurse=True)

    def __setattr__(self, key: str, val: Any) -> None:
        """
        If val is a Parameter or Module, store it in the appropriate _parameters or _modules dict.
        Otherwise, call __setattr__ from the superclass.
        """
        if isinstance(val, Parameter):
            self._parameters[key] = val
        elif isinstance(val, Module):
            self._modules[key] = val
        super().__setattr__(key, val)

    def __call__(self, *args, **kwargs):
        return self.forward(*args, **kwargs)

    def forward(self):
        raise NotImplementedError("Subclasses must implement forward!")

    def __repr__(self):
        _indent = lambda s_, nSpaces: re.sub("\n", "\n" + (" " * nSpaces), s_)
        lines = [f"({key}): {_indent(repr(module), 2)}" for key, module in self._modules.items()]
        return "".join(
            [
                self.__class__.__name__ + "(",
                "\n  " + "\n  ".join(lines) + "\n" if lines else "",
                ")",
            ]
        )


class TestInnerModule(Module):
    def __init__(self):
        super().__init__()
        self.param1 = Parameter(Tensor([1.0]))
        self.param2 = Parameter(Tensor([2.0]))


class TestModule(Module):
    def __init__(self):
        super().__init__()
        self.inner = TestInnerModule()
        self.param3 = Parameter(Tensor([3.0]))


mod = TestModule()
assert list(mod.modules()) == [mod.inner]
assert list(mod.parameters()) == [mod.param3, mod.inner.param1, mod.inner.param2]
print("Manually verify that the repr looks reasonable:")
print(mod)
print("All tests for `Module` passed!")

Manually verify that the repr looks reasonable:
TestModule(
  (inner): TestInnerModule()
)
All tests for `Module` passed!


### Exercise - implement `Linear`

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵🔵🔵⚪
> 
> You should spend up to 20-25 minutes on this exercise.
> ```

Now, let's go one level of abstraction higher and create a `Linear` module. This should inherit from `Module` and have `__init__` & `forward` methods just like your linear module inheriting from `nn.Module` in previous exercises. In fact, your code can probably be extremely similar to the time you implemented `Linear` in the earlier exercises, except you'll need to use methods we've defined already. You should be able to do everything you need in `forward` using just the matmul operator `@`, the transpose operator `.T` (which is equivalent to `.permute(-1, -2)` as you can see in the tensor class above) and standard tensor addition `+`.

To restate the task in case you don't remember it from the previous exercises, you should:

- Define `self.weight` and `self.bias` in `__init__`, with both tensors having a uniform distribution in the range `[-sf, sf]` where `sf = 1/sqrt(in_features)`,
- Write the appropriate affine operation in `forward`, i.e. multiplying by `self.weight` and adding `self.bias` if it exists.

Don't forget to wrap your weights as `Parameter(Tensor(...))`.

In [31]:
class Linear(Module):
    weight: Parameter
    bias: Parameter | None

    def __init__(self, in_features: int, out_features: int, bias=True):
        """
        A simple linear (technically, affine) transformation.

        The fields should be named `weight` and `bias` for compatibility with PyTorch.
        If `bias` is False, set `self.bias` to None.
        """
        super().__init__()
        self.in_features = in_features
        self.out_features = out_features

        # w = np.random.random((out_features, in_features)) / np.sqrt(in_features)
        # self.weight = Parameter(Tensor(w))

        # if bias:
        #     b = np.random.random(out_features) / np.sqrt(in_features)
        #     self.bias = Parameter(Tensor(b))
        # else:
        #     self.bias = None

        sf = in_features**-0.5
        self.weight = Parameter(Tensor(sf * (2 * np.random.rand(out_features, in_features) - 1)))
        self.bias = Parameter(Tensor(sf * (2 * np.random.rand(out_features) - 1))) if bias else None

    def forward(self, x: Tensor) -> Tensor:
        """
        x: shape (*, in_features)
        Return: shape (*, out_features)
        """
        out = x @ self.weight.T
        if self.bias is not None:
            out = out + self.bias
        return out

    def extra_repr(self) -> str:
        return (
            f"in_features={self.in_features}, out_features={self.out_features}, "
            f"bias={self.bias is not None}"
        )


linear = Linear(3, 4)
assert isinstance(linear.weight, Tensor)
assert linear.weight.requires_grad

input = Tensor([[1.0, 2.0, 3.0]])
output = linear(input)
assert output.requires_grad

expected_output = input @ linear.weight.T + linear.bias
np.testing.assert_allclose(output.array, expected_output.array)

print("All tests for `Linear` passed!")

All tests for `Linear` passed!


<details><summary>Solution</summary>

```python
class Linear(Module):
    weight: Parameter
    bias: Parameter | None

    def __init__(self, in_features: int, out_features: int, bias=True):
        """
        A simple linear (technically, affine) transformation.

        The fields should be named `weight` and `bias` for compatibility with PyTorch.
        If `bias` is False, set `self.bias` to None.
        """
        super().__init__()
        self.in_features = in_features
        self.out_features = out_features

        sf = in_features**-0.5
        self.weight = Parameter(Tensor(sf * (2 * np.random.rand(out_features, in_features) - 1)))
        self.bias = Parameter(Tensor(sf * (2 * np.random.rand(out_features) - 1))) if bias else None

    def forward(self, x: Tensor) -> Tensor:
        """
        x: shape (*, in_features)
        Return: shape (*, out_features)
        """
        out = (
            x @ self.weight.T
        )  # transpose has been defined as .permute(-1, -2), see the `Tensor` class
        if self.bias is not None:
            out = out + self.bias
        return out

    def extra_repr(self) -> str:
        return (
            f"in_features={self.in_features}, out_features={self.out_features}, "
            f"bias={self.bias is not None}"
        )
```
</details>

Finally, for the sake of completeness, we'll define a `ReLU` module:

In [32]:
class ReLU(Module):
    def forward(self, x: Tensor) -> Tensor:
        return relu(x)

Now we can define a MLP suitable for classifying MNIST, with zero PyTorch dependency!

In [33]:
class MLP(Module):
    def __init__(self):
        super().__init__()
        self.linear1 = Linear(28 * 28, 64)
        self.linear2 = Linear(64, 64)
        self.relu1 = ReLU()
        self.relu2 = ReLU()
        self.output = Linear(64, 10)

    def forward(self, x: Tensor) -> Tensor:
        x = x.reshape((x.shape[0], 28 * 28))
        x = self.relu1(self.linear1(x))
        x = self.relu2(self.linear2(x))
        x = self.output(x)
        return x

### Exercise - implement `cross_entropy`

> ```yaml
> Difficulty: 🔴🔴🟠⚪⚪
> Importance: 🔵🔵🔵⚪⚪
> 
> You should spend up to 10-15 minutes on this exercise.
> ```

Make use of your integer array indexing to implement `cross_entropy`. See the documentation page [here](https://pytorch.org/docs/stable/generated/torch.nn.CrossEntropyLoss.html).

We discussed this briefly in the section on indexing earlier, but the kind of indexing you should be doing on your logprobs is `logprobs[range(batch_size), true_labels]`, since this is equivalent to returning the vector of length `batch_size` with elements `[logprobs[0, true_labels[0]], logprobs[1, true_labels[1]], ...]`. Rather than using `range`, you should be using the `arange` function we've provided for you (this is equivalent to torch's `torch.arange` function, and is defined just below the `Tensor` class).

Note - if you're using the `exp` function, it's usually good to make your implementation numerically stable (since taking the exponential of large numbers is prone to overflow). The common solution here is to subtract the maximum value of the tensor from all elements. However, you don't need to worry about that here (consider it a bonus exercise).

In [34]:
def cross_entropy(logits: Tensor, true_labels: Tensor) -> Tensor:
    """Like torch.nn.functional.cross_entropy with reduction='none'.

    logits: shape (batch, classes)
    true_labels: shape (batch,). Each element is the index of the correct label in the logits.

    Return: shape (batch, ) containing the per-example loss.
    """

    logprobs = logits - logits.exp().sum(dim=-1, keepdim=True).log()
    return -logprobs[arange(0, logits.shape[0]), true_labels]


# tests.test_cross_entropy(Tensor, cross_entropy)
logits = Tensor(
    [
        [0, -100, -100, -100],  # equivalent to certainty of class=0
        [1 / 4, 1 / 4, 1 / 4, 1 / 4],  # uniform over all classes
        [0, 0, 0, -100],  # equivalent to uniform over first 3 classes
        [1000, 0, 0, 0],  # unstable test case
    ]
)
true_labels = Tensor([0, 0, 0, 0])
expected = Tensor([0.0, np.log(4), np.log(3), 0])
# with warnings.catch_warnings():
#     warnings.simplefilter("ignore", RuntimeWarning)

# First test: numerically stable
# print("Testing for numerically stable cases ... ", end="")
actual = cross_entropy(logits[:3], true_labels[:3])
np.testing.assert_allclose(actual.array, expected[:3].array)
# print("passed!")

# # Second test: unstable (will generate nans if not handled correctly)
# print("Testing for numerically unstable cases ... ", end="")
# actual = cross_entropy(logits[3:], true_labels[3:])
# np.testing.assert_allclose(actual.array, expected[3:].array)
# print("passed!")

print("All tests in `test_cross_entropy` passed!")

Tensor(array([[ 0.0e+00, -1.0e+02, -1.0e+02, -1.0e+02],
       [ 2.5e-01,  2.5e-01,  2.5e-01,  2.5e-01],
       [ 0.0e+00,  0.0e+00,  0.0e+00, -1.0e+02],
       [ 1.0e+03,  0.0e+00,  0.0e+00,  0.0e+00]], dtype=float32), requires_grad=False) slice(None, 3, None)
Tensor(array([0, 0, 0, 0]), requires_grad=False) slice(None, 3, None)
Tensor(array([[   0.       , -100.       , -100.       , -100.       ],
       [  -1.3862944,   -1.3862944,   -1.3862944,   -1.3862944],
       [  -1.0986123,   -1.0986123,   -1.0986123, -101.09861  ]],
      dtype=float32), requires_grad=False) (Tensor(array([0, 1, 2]), requires_grad=False), Tensor(array([0, 0, 0]), requires_grad=False))
Tensor(array([0.       , 1.3862944, 1.0986123, 0.       ], dtype=float32), requires_grad=False) slice(None, 3, None)
All tests in `test_cross_entropy` passed!


<details>
<summary>Help - I'm not sure how to get logprobs from logits.</summary>

They're equal up to a constant: `logprobs = logits - log(sum(exp(logits)))` (where the sum is over the last dimension).

To see why this is true: let's define `C = logits - logprobs`. We know `sum(exp(logits - C)) = sum(exp(logprobs)) = 1` (this is by definition of `logprobs`). Factoring out the `exp(-C)` term, we get `exp(C) = sum(exp(logits))`, hence `C = log(sum(exp(logits)))` as required.

</details>

<details>
<summary>Solution</summary>

```python
def cross_entropy(logits: Tensor, true_labels: Tensor) -> Tensor:
    """Like torch.nn.functional.cross_entropy with reduction='none'.

    logits: shape (batch, classes)
    true_labels: shape (batch,). Each element is the index of the correct label in the logits.

    Return: shape (batch, ) containing the per-example loss.
    """
    batch_size = logits.shape[0]
    logprobs = logits - logits.exp().sum(-1, keepdim=True).log()
    return -logprobs[arange(0, batch_size), true_labels]
```

or alternatively we can solve a slightly different way, which is still equivalent:

```python
true = logits[arange(0, batch_size), true_labels]
return -log(exp(true) / exp(logits).sum(1))
```

</details>

## `NoGrad` context manager

The last thing our backpropagation system needs is the ability to turn it off completely like `torch.no_grad` (or `torch.inference_mode`). We've given you an implementation below, which works by modifying the global `grad_tracking_enabled` variable. 

A few notes on the actual python here (again for people who are more familiar with Python and understand it can skip this):

- The `global` keyword is required in order to modify the global `grad_tracking_enabled` variable. We can still reference its value without this keyword, but we wouldn't be able to change it.
- The special `__enter__` and `__exit__` methods are part of the protocol for context managers, which is a more pythonic way of doing this kind of thing. If we have a context manager block like `with NoGrad(): ...`, then we'll run `NoGrad().__enter__()` before any of the code in this block, and `NoGrad().__exit__()` after the block finishes.

In [35]:
class NoGrad:
    """Context manager that disables grad inside the block. Like torch.no_grad."""

    was_enabled: bool

    def __enter__(self):
        """
        Method which is called whenever the context manager is entered, i.e. at the start of the
        `with NoGrad():` block. This disables gradient tracking (but stores the value it had before,
        so we can set it back to this on exit).
        """
        global grad_tracking_enabled
        self.was_enabled = grad_tracking_enabled
        grad_tracking_enabled = False

    def __exit__(self, type, value, traceback):
        """
        Method which is called whenever we exit the context manager. This sets the global
        `grad_tracking_enabled` variable back to the value it had before we entered the context
        manager.
        """
        global grad_tracking_enabled
        grad_tracking_enabled = self.was_enabled


assert grad_tracking_enabled
with NoGrad():
    assert not grad_tracking_enabled
assert grad_tracking_enabled
print(
    "Verified that we've disabled gradients inside `NoGrad`, then set back to its previous "
    "value once we exit."
)

Verified that we've disabled gradients inside `NoGrad`, then set back to its previous value once we exit.


### Exercise - implement `SGD`

> ```yaml
> Difficulty: 🔴🔴🔴⚪⚪
> Importance: 🔵🔵🔵⚪⚪
> 
> You should spend up to 10-20 minutes on this exercise.
> ```

In today's final exercise, you should implement the `SGD` class methods `zero_grad` and `step`. This should be pretty familiar if you've gone through yesterday's exercises on optimizers (although without all the bells and whistles from those exercises, because we're literally just implementing plain SGD with no momentum, weight decay or anything).

Important note - in yesterday's exercises it was important to use inplace operations, so we would actually modify the existing tensor data rather than creating new tensors, and this is also the case here. The inplace operation `+=` is supported, since under the hood this calls `__iadd__` which we've defined in our `Tensor` class (same for subtraction, the underlying method here is `__isub__`). Note that we did discuss earlier how inplace operations are very risky for backprop, this is generally true however here we're using it for parameter updates which aren't meant to be differentiated and which are performed just before zeroing all gradients - this makes it safe in this particular context.

In [36]:
class SGD:
    def __init__(self, params: Iterable[Parameter], lr: float):
        """Vanilla SGD with no additional features."""
        self.params = list(params)
        self.lr = lr
        self.b = [None for _ in self.params]

    def zero_grad(self) -> None:
        """Iterates through params, and sets all grads to None."""
        for p in self.params:
            p.grad = None

    def step(self) -> None:
        """Iterates through params, and updates each of them by subtracting `param.grad * lr`."""
        with NoGrad():
            for p in self.params:
                assert p.grad is not None, f"p.requires_grad={p.requires_grad}"
                p -= p.grad * self.lr


tests.test_sgd(Parameter, Tensor, SGD)

All tests for `SGD` passed!


<details><summary>Solution</summary>

```python
class SGD:
    def __init__(self, params: Iterable[Parameter], lr: float):
        """Vanilla SGD with no additional features."""
        self.params = list(params)
        self.lr = lr
        self.b = [None for _ in self.params]

    def zero_grad(self) -> None:
        """Iterates through params, and sets all grads to None."""
        for p in self.params:
            p.grad = None

    def step(self) -> None:
        """Iterates through params, and updates each of them by subtracting `param.grad * lr`."""
        with NoGrad():
            for p in self.params:
                p -= p.grad * self.lr
```
</details>

## Training Your Network

We've already looked at data loading and training loops earlier in the course, so we'll provide a minimal version of these today as well as the data loading code.

In [37]:
train_loader, test_loader = get_mnist()
visualize(train_loader)

Preprocessing data...


Test data: 100%|██████████| 10000/10000 [00:00<00:00, 45341.18it/s]


To finish the day, below is some code for a training/testing loop for MNIST images, which also logs & plots the results.

Note, it's normal to encounter some bugs and glitches at this point - just go back and fix them until everything runs! Because backprop is annoying and fiddly and depends heavily on exactly how the implementation works (with too many edge cases to test all of them), you may have to resort to replacing your code with the reference solution until you find the source of the error - this is a bit frustrating, but we'd be lying if we said ML isn't without its share of slow debugging sessions!

In [38]:
def train(
    model: MLP,
    train_loader: DataLoader,
    optimizer: SGD,
    epoch: int,
    train_loss_list: list | None = None,
):
    print(f"Epoch: {epoch}")
    progress_bar = tqdm(train_loader)
    for data, target in progress_bar:
        data, target = Tensor(data.numpy()), Tensor(target.numpy())
        optimizer.zero_grad()
        output = model(data)
        loss = cross_entropy(output, target).sum() / len(output)
        loss.backward()
        progress_bar.set_description(f"Train set: Avg loss: {loss.item():.3f}")
        optimizer.step()
        if train_loss_list is not None:
            train_loss_list.append(loss.item())


def test(model: MLP, test_loader: DataLoader, test_accuracy_list: list | None = None):
    test_loss = 0
    test_accuracy = 0
    with NoGrad():
        for data, target in test_loader:
            data, target = Tensor(data.numpy()), Tensor(target.numpy())
            output: Tensor = model(data)
            test_loss += cross_entropy(output, target).sum().item()
            pred = output.argmax(dim=1, keepdim=True)
            test_accuracy += (pred == target.reshape(pred.shape)).sum().item()
    n_data = len(test_loader.dataset)
    test_loss /= n_data
    print(
        f"Test set:  Avg loss: {test_loss:.3f}, Accuracy: {test_accuracy}/{n_data} "
        f"({test_accuracy / n_data:.1%})"
    )
    if test_accuracy_list is not None:
        test_accuracy_list.append(test_accuracy / n_data)


num_epochs = 5
model = MLP()
start = time.time()
train_loss_list = []
test_accuracy_list = []
optimizer = SGD(model.parameters(), 0.01)
for epoch in range(num_epochs):
    train(model, train_loader, optimizer, epoch, train_loss_list)
    test(model, test_loader, test_accuracy_list)
    
print(f"\nCompleted in {time.time() - start: .2f}s")

Epoch: 0


Train set: Avg loss: 2.300:   3%|▎         | 4/118 [00:00<00:03, 37.57it/s]

Tensor(array([[-2.299943 , -2.3495545, -2.338394 , ..., -2.1801422, -2.2315998,
        -2.3077364],
       [-2.275294 , -2.289484 , -2.3036883, ..., -2.2109418, -2.253685 ,
        -2.3163168],
       [-2.3089776, -2.338474 , -2.2239766, ..., -2.1487591, -2.293903 ,
        -2.3215642],
       ...,
       [-2.3637326, -2.3944924, -2.3504696, ..., -2.205048 , -2.2136858,
        -2.28388  ],
       [-2.3443809, -2.3639371, -2.2241094, ..., -2.2054224, -2.267664 ,
        -2.2045853],
       [-2.3670921, -2.3956125, -2.3692565, ..., -2.1962612, -2.277049 ,
        -2.4178824]], dtype=float32), requires_grad=True) (Tensor(array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52,  53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,
        65, 

Train set: Avg loss: 2.296:   8%|▊         | 9/118 [00:00<00:02, 43.73it/s]

Tensor(array([[-2.3050165, -2.2568858, -2.2957857, ..., -2.2480857, -2.2457933,
        -2.3244245],
       [-2.37841  , -2.3282928, -2.2713623, ..., -2.2068787, -2.301724 ,
        -2.238103 ],
       [-2.3597612, -2.3843136, -2.315166 , ..., -2.1600673, -2.2905123,
        -2.339905 ],
       ...,
       [-2.3556995, -2.3637097, -2.360222 , ..., -2.2052279, -2.2100444,
        -2.2717252],
       [-2.2805045, -2.3686   , -2.2787292, ..., -2.1966271, -2.2514064,
        -2.2554471],
       [-2.2920728, -2.3066509, -2.2873821, ..., -2.2492104, -2.270681 ,
        -2.2761354]], dtype=float32), requires_grad=True) (Tensor(array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52,  53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,
        65, 

...

Tensor(array([[ -9.089392  ,  -7.7571282 ,  -0.03136444, ..., -11.028791  ,
         -6.2897434 ,  -8.441237  ],
       [ -5.6850014 ,  -9.149522  ,  -7.088815  , ...,  -0.2678237 ,
         -6.261397  ,  -1.601125  ],
       [ -6.537759  ,  -5.587435  ,  -3.0897856 , ...,  -7.1621842 ,
         -5.8958864 ,  -6.9056845 ],
       ...,
       [ -8.415758  , -13.268588  ,  -7.7109175 , ...,  -6.7826104 ,
         -5.4241056 ,  -1.9178987 ],
       [ -7.780764  ,  -8.914963  ,  -5.499035  , ...,  -3.518642  ,
         -5.5795326 ,  -1.4921145 ],
       [ -6.611562  ,  -1.1514578 ,  -3.4709895 , ...,  -5.943383  ,
         -0.8030257 ,  -5.194641  ]], dtype=float32), requires_grad=True) (Tensor(array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52, 

Train set: Avg loss: 0.470:  89%|████████▉ | 105/118 [00:03<00:00, 34.29it/s]

Tensor(array([[ -9.716406  ,  -0.02920961,  -4.5162554 , ...,  -6.7347274 ,
         -5.177143  ,  -7.8665624 ],
       [ -7.9180155 , -11.118706  ,  -7.553564  , ...,  -4.5349903 ,
         -5.607207  ,  -1.1123333 ],
       [ -5.6604805 ,  -5.5224547 ,  -1.3456633 , ...,  -6.9938755 ,
         -5.226178  ,  -6.4829054 ],
       ...,
       [ -3.2562125 ,  -7.418148  ,  -6.434478  , ...,  -4.410464  ,
         -3.2893934 ,  -3.2115388 ],
       [ -8.660235  ,  -9.120533  ,  -3.7959714 , ...,  -5.3368673 ,
         -5.125876  ,  -2.7031593 ],
       [ -7.2067266 ,  -6.161022  ,  -3.981381  , ...,  -6.703995  ,
         -2.45445   ,  -6.2313595 ]], dtype=float32), requires_grad=True) (Tensor(array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52, 

Train set: Avg loss: 0.490: 100%|██████████| 118/118 [00:03<00:00, 32.96it/s]


Tensor(array([[-6.5432816e+00, -3.7369554e+00, -5.5403104e+00, ...,
        -2.6674225e+00, -2.0150948e+00, -4.7951245e-01],
       [-1.3948441e-02, -1.4953245e+01, -9.1166058e+00, ...,
        -6.2809916e+00, -7.9020472e+00, -7.6647444e+00],
       [-6.4198050e+00, -9.0718670e+00, -8.3805628e+00, ...,
        -1.6994905e-01, -6.4838448e+00, -2.0744891e+00],
       ...,
       [-7.0827808e+00, -6.4825444e+00, -4.8151555e+00, ...,
        -1.1219978e-01, -4.1519985e+00, -2.6908896e+00],
       [-3.7279129e-03, -1.7952869e+01, -8.3960037e+00, ...,
        -9.6356049e+00, -8.9135857e+00, -8.9864063e+00],
       [-3.7821047e+00, -1.2628450e+01, -6.4597569e+00, ...,
        -4.0909181e+00, -3.6952314e+00, -2.6010084e-01]], dtype=float32), requires_grad=True) (Tensor(array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39, 

In [39]:
line(
    [train_loss_list, test_accuracy_list],
    x_max=num_epochs,
    yaxis2_range=[0, 1],
    use_secondary_yaxis=True,
    labels={"x": "Batches seen", "y1": "Cross entropy loss", "y2": "Test accuracy"},
    title="MLP training on MNIST from scratch!",
    width=800,
)

Note - this training loop (if done correctly) will look to the one we used in earlier sections is that we're using SGD rather than Adam. You can try adapting your Adam code from the previous day's exercises, and get the same results as you have in earlier sections.

If it works then congratulations - you've implemented a fully-functional autograd system!

# Bonus

Congratulations on finishing the day's main content! Here are a few more bonus things for you to explore.

### In-Place Operation Warnings

The most severe issue with our current system is that it can silently compute the wrong gradients when in-place operations are used. Have a look at how [PyTorch handles it](https://pytorch.org/docs/stable/notes/autograd.html#in-place-operations-with-autograd) and implement a similar system yourself so that it either computes the right gradients, or raises a warning.

### In-Place `ReLU`

Instead of implementing ReLU in terms of maximum, implement your own forward and backward functions that support `inplace=True`.

### Backward for `einsum`

Write the backward pass for your equivalent of `torch.einsum`.

### Reuse of Module during forward

Consider the following MLP, where the same `nn.ReLU` instance is used twice in the forward pass. Without running the code, explain whether this works correctly or not with reference to the specifics of your implementation.

```python
class MyModule(Module):
    def __init__(self):
        super().__init__()
        self.linear1 = Linear(28*28, 64)
        self.linear2 = Linear(64, 64)
        self.linear3 = Linear(64, 10)
        self.relu = ReLU()
    def forward(self, x):
        x = self.relu(self.linear1(x))
        x = self.relu(self.linear2(x))
        return self.linear3(x)
```

<details>
<summary>Answer (what you should find)</summary>

This implementation will work correctly.

The danger of reusing modules is that you'd be creating a cyclical computational graph (because the same parameters would appear twice), but the `ReLU` module doesn't have any parameters (or any internal state), so this isn't a problem. It's effectively just a wrapper for the `relu` function, and you could replace `self.relu` with applying the `relu` function directly without changing the model's behaviour.

This is slightly different if we're thinking about adding **hooks** to our model. Hooks are functions that are called during the forward or backward pass, and they can be used to inspect the state of the model during training. We generally want each hook to be associated with a single position in the model, rather than being called at two different points.
</details>

### Convolutional layers

Now that you've implemented a linear layer, it should be relatively straightforward to take your convolutions code from day 2 and use it to make a convolutional layer. How much better performance do you get on the MNIST task once you replace your first two linear layers with convolutions?

### ResNet Support

Make a list of the features that would need to be implemented to support ResNet inference, and training. It will probably take too long to do all of them, but pick some interesting features to start implementing.

### Central Difference Checking

Write a function that compares the gradients from your backprop to a central difference method. See [Wikipedia](https://en.wikipedia.org/wiki/Finite_difference) for more details.

### Non-Differentiable Function Support

Your `Tensor` does not currently support equivalents of `torch.all`, `torch.any`, `torch.floor`, `torch.less`, etc. which are non-differentiable functions of Tensors. Implement them so that they are usable in computational graphs, but gradients shouldn't flow through them (their contribution is zero).

### Differentiation wrt Keyword Arguments

In the real PyTorch, you can sometimes pass tensors as keyword arguments and differentiation will work, as in `t.add(other=t.tensor([3,4]), input=t.tensor([1,2]))`. In other similar looking cases like `t.dot`, it raises an error that the argument must be passed positionally. Decide on a desired behavior in your system and implement and test it.

### `torch.stack`

So far we've registered a separate backwards for each input argument that could be a Tensor. This is problematic if the function can take any number of tensors like `torch.stack` or `numpy.stack`. Think of and implement the backward function for stack. It may require modification to your other code.